In [1]:
import pandas as pd
# import datetime
# import random
import os

from bokeh.plotting import figure
# from bokeh.palettes import Category20
# from bokeh.layouts import gridplot
from bokeh.io import output_notebook, show

output_notebook()

# pd.set_option('display.max_columns', None)
# pd.set_option('display.width', 1000)

# palette = Category20[20]

os.chdir("/home/tales/dev/master/mdc_analysis/")
print("working dir", os.getcwd())

# from src.dao.dbdao import DBDAO
from src.dao import csv_dao
from src.plot import plot
from src.utils import geo
from src.entity.geo_circle import GeoCircle 
# from src.utils.time_utils import diff_between_dates


from sklearn.cluster import KMeans

import gc

# pd.set_option('display.float_format', lambda x: '%.3f' % x)

Loading BokehJS ...

working dir /home/tales/dev/master/mdc_analysis


In [2]:
stop_regions = csv_dao.load_all_users_stop_regions_centroids(verbose=True)
stop_regions = stop_regions[stop_regions["tag"] == ""]

User 6189 data loaded
User 5936 data loaded
User 6087 data loaded
User 5973 data loaded
User 6085 data loaded
User 6074 data loaded
User 6012 data loaded
User 5982 data loaded
User 5948 data loaded
User 5974 data loaded
User 6090 data loaded
User 6199 data loaded
User 6068 data loaded
User 6024 data loaded
User 5976 data loaded
User 6094 data loaded
User 5941 data loaded
User 5995 data loaded
User 5962 data loaded
User 6093 data loaded
User 6033 data loaded
User 6079 data loaded
User 6038 data loaded
User 6175 data loaded
User 6042 data loaded
User 5924 data loaded
User 6083 data loaded
User 6178 data loaded
User 5958 data loaded
User 6086 data loaded
User 6100 data loaded
User 5945 data loaded
User 5925 data loaded
User 5935 data loaded
User 6172 data loaded
User 5955 data loaded
User 6073 data loaded
User 5980 data loaded
User 6010 data loaded
User 5993 data loaded
User 6037 data loaded
User 5979 data loaded
User 5966 data loaded
User 5985 data loaded
User 5967 data loaded
User 5970 

In [3]:
stop_regions = stop_regions.set_index("sr_id", drop=False)
stop_regions.sample(6)

latitude  local_end_time  local_start_time  longitude     sr_id tag  \
sr_id                                                                           
6094_398  46.51000    1.275903e+09      1.275902e+09    6.56000  6094_398       
6004_105  46.60000    1.257537e+09      1.257536e+09    6.60000  6004_105       
5988_462  46.20484    1.281633e+09      1.281631e+09    6.14033  5988_462       
5948_882  46.09656    1.290539e+09      1.290537e+09    7.06270  5948_882       
5972_586  46.52582    1.286643e+09      1.286642e+09    6.62521  5972_586       
6178_124  46.48772    1.271437e+09      1.271435e+09    6.73075  6178_124       

         user_id  
sr_id             
6094_398    6094  
6004_105    6004  
5988_462    5988  
5948_882    5948  
5972_586    5972  
6178_124    6178

In [4]:
stop_regions = stop_regions[["latitude", "longitude", "sr_id", "tag", "user_id"]]
stop_regions = csv_dao.unique_stop_regions(stop_regions)
gc.collect()
print(len(stop_regions))

40766


## Grouping Stop Regions into Request Circles

Trying to group Stop Regions in order to reduce Google Places requests

In [7]:
def data_frame_to_geo_circle(data):
    return data.apply(lambda row : GeoCircle(row["latitude"], row["longitude"], radius_m=50, id=row.index,
                                                 data={"tag": row["tag"], "user_id": row["user_id"]}), axis=1)

def slice_geo_data(data, center, search_tolerance):
    min_lats = center.center_lat - search_tolerance
    max_lats = center.center_lat + search_tolerance
    min_lons = center.center_lon - search_tolerance
    max_lons = center.center_lon + search_tolerance

    return data[(data["latitude"] >= min_lats)  & (data["latitude"] <= max_lats) &
                (data["longitude"] >= min_lons) & (data["longitude"] <= max_lons)]

def ckeck_circle_in_list(circle, list_circles):
    for c in list_circles:
        if c["circle"].id == circle["circle"].id:
            return True
    return False

def group_geo_circles(data, request_radius, search_tolerance=0.0015, verbose=False):
    request_circles = []
    data["checked"] = False
    
    counter = 0
    indexes = data.index.tolist()
    
    for index_i in indexes:
        counter += 1
        print(counter, index_i)
        
        c = data.loc[index_i]
        
        if c["checked"]:
            continue
        
        request_circle = GeoCircle(c["circle"].center_lat, c["circle"].center_lon, 
                                   radius_m=request_radius, id="rc_" + c["sr_id"])
        
        request_circle.sr = pd.DataFrame()
        request_circle.sr = request_circle.sr.append(c)
        
        request_circles.append(request_circle)
        
        for index_j, neighbor in slice_geo_data(data, request_circle, search_tolerance).iterrows():
            if (request_circle.contains_geo_circle(neighbor["circle"])):
                request_circle.sr = request_circle.sr.append(neighbor)
                
                data.loc[data.index == index_j, 'checked'] = True #updating centroid as checked
    
    csv_dao.save_request_circles(request_circles, request_radius, search_tolerance)
        
    return request_circles

In [8]:
stop_regions["circle"] = data_frame_to_geo_circle(stop_regions)

In [9]:
search_tolerance = 0.0006
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_50 = group_geo_circles(stop_regions, 50, search_tolerance)
print("{} request circles".format(len(request_circles_50)))

d: 81.15379220334191
1 6189_0
2 6189_1
3 6189_10
4 6189_100
5 6189_101
6 6189_102
7 6189_103
8 6189_104
9 6189_107
10 6189_108
11 6189_109
12 6189_11
13 6189_110
14 6189_111
15 6189_115
16 6189_117
17 6189_119
18 6189_12
19 6189_120
20 6189_121
21 6189_122
22 6189_124
23 6189_125
24 6189_126
25 6189_127
26 6189_128
27 6189_129
28 6189_130
29 6189_132
30 6189_134
31 6189_137
32 6189_138
33 6189_14
34 6189_140
35 6189_141
36 6189_142
37 6189_143
38 6189_144
39 6189_145
40 6189_146
41 6189_147
42 6189_149
43 6189_150
44 6189_151
45 6189_152
46 6189_153
47 6189_157
48 6189_158
49 6189_160
50 6189_161
51 6189_163
52 6189_166
53 6189_167
54 6189_168
55 6189_171
56 6189_178
57 6189_179
58 6189_184
59 6189_187
60 6189_188
61 6189_189
62 6189_19
63 6189_190
64 6189_191
65 6189_192
66 6189_193
67 6189_194
68 6189_195
69 6189_196
70 6189_201
71 6189_203
72 6189_204
73 6189_209
74 6189_211
75 6189_212
76 6189_214
77 6189_215
78 6189_216
79 6189_217
80 6189_218
81 6189_219
82 6189_22
83 6189_220
84

645 5936_731
646 5936_732
647 5936_74
648 5936_741
649 5936_746
650 5936_748
651 5936_75
652 5936_753
653 5936_755
654 5936_76
655 5936_78
656 5936_83
657 5936_84
658 5936_85
659 5936_88
660 5936_89
661 5936_90
662 5936_93
663 5936_95
664 5936_97
665 6087_106
666 6087_108
667 6087_11
668 6087_129
669 6087_133
670 6087_134
671 6087_141
672 6087_147
673 6087_148
674 6087_149
675 6087_150
676 6087_151
677 6087_16
678 6087_161
679 6087_163
680 6087_168
681 6087_169
682 6087_170
683 6087_172
684 6087_173
685 6087_174
686 6087_177
687 6087_178
688 6087_179
689 6087_180
690 6087_181
691 6087_182
692 6087_186
693 6087_196
694 6087_198
695 6087_2
696 6087_20
697 6087_211
698 6087_213
699 6087_222
700 6087_223
701 6087_224
702 6087_225
703 6087_227
704 6087_232
705 6087_233
706 6087_234
707 6087_235
708 6087_237
709 6087_254
710 6087_255
711 6087_256
712 6087_257
713 6087_258
714 6087_275
715 6087_276
716 6087_280
717 6087_283
718 6087_284
719 6087_285
720 6087_286
721 6087_287
722 6087_288
723 

1231 5973_691
1232 5973_70
1233 5973_71
1234 5973_72
1235 5973_73
1236 5973_730
1237 5973_731
1238 5973_732
1239 5973_733
1240 5973_74
1241 5973_75
1242 5973_76
1243 5973_767
1244 5973_768
1245 5973_769
1246 5973_77
1247 5973_770
1248 5973_771
1249 5973_772
1250 5973_773
1251 5973_774
1252 5973_775
1253 5973_776
1254 5973_777
1255 5973_778
1256 5973_779
1257 5973_78
1258 5973_780
1259 5973_781
1260 5973_782
1261 5973_783
1262 5973_784
1263 5973_785
1264 5973_786
1265 5973_787
1266 5973_788
1267 5973_789
1268 5973_79
1269 5973_790
1270 5973_791
1271 5973_792
1272 5973_793
1273 5973_794
1274 5973_795
1275 5973_796
1276 5973_797
1277 5973_80
1278 5973_800
1279 5973_81
1280 5973_814
1281 5973_815
1282 5973_85
1283 5973_859
1284 5973_86
1285 5973_87
1286 5973_88
1287 5973_89
1288 5973_90
1289 5973_91
1290 5973_951
1291 5973_956
1292 5973_957
1293 5973_958
1294 5973_959
1295 5973_981
1296 5973_982
1297 6085_10
1298 6085_100
1299 6085_1000
1300 6085_1003
1301 6085_1004
1302 6085_1005
1303 608

1802 6085_539
1803 6085_54
1804 6085_540
1805 6085_541
1806 6085_542
1807 6085_543
1808 6085_544
1809 6085_545
1810 6085_546
1811 6085_548
1812 6085_549
1813 6085_55
1814 6085_551
1815 6085_552
1816 6085_554
1817 6085_556
1818 6085_559
1819 6085_56
1820 6085_562
1821 6085_563
1822 6085_564
1823 6085_572
1824 6085_573
1825 6085_576
1826 6085_589
1827 6085_59
1828 6085_590
1829 6085_591
1830 6085_593
1831 6085_6
1832 6085_601
1833 6085_602
1834 6085_603
1835 6085_604
1836 6085_608
1837 6085_609
1838 6085_610
1839 6085_611
1840 6085_612
1841 6085_613
1842 6085_614
1843 6085_615
1844 6085_62
1845 6085_624
1846 6085_63
1847 6085_630
1848 6085_631
1849 6085_632
1850 6085_633
1851 6085_634
1852 6085_635
1853 6085_636
1854 6085_64
1855 6085_641
1856 6085_643
1857 6085_646
1858 6085_647
1859 6085_65
1860 6085_653
1861 6085_654
1862 6085_655
1863 6085_656
1864 6085_657
1865 6085_66
1866 6085_661
1867 6085_662
1868 6085_663
1869 6085_67
1870 6085_670
1871 6085_674
1872 6085_676
1873 6085_677
1874

2403 5948_425
2404 5948_426
2405 5948_427
2406 5948_428
2407 5948_429
2408 5948_431
2409 5948_432
2410 5948_433
2411 5948_434
2412 5948_435
2413 5948_436
2414 5948_437
2415 5948_438
2416 5948_439
2417 5948_440
2418 5948_441
2419 5948_442
2420 5948_443
2421 5948_444
2422 5948_45
2423 5948_450
2424 5948_451
2425 5948_467
2426 5948_48
2427 5948_491
2428 5948_492
2429 5948_493
2430 5948_494
2431 5948_495
2432 5948_498
2433 5948_499
2434 5948_5
2435 5948_500
2436 5948_511
2437 5948_512
2438 5948_513
2439 5948_514
2440 5948_515
2441 5948_516
2442 5948_517
2443 5948_518
2444 5948_519
2445 5948_52
2446 5948_520
2447 5948_521
2448 5948_522
2449 5948_523
2450 5948_53
2451 5948_533
2452 5948_534
2453 5948_535
2454 5948_536
2455 5948_537
2456 5948_538
2457 5948_539
2458 5948_54
2459 5948_548
2460 5948_55
2461 5948_554
2462 5948_555
2463 5948_556
2464 5948_557
2465 5948_56
2466 5948_57
2467 5948_574
2468 5948_58
2469 5948_585
2470 5948_586
2471 5948_59
2472 5948_6
2473 5948_60
2474 5948_600
2475 59

...

38138 5965_619
38139 5965_621
38140 5965_622
38141 5965_623
38142 5965_624
38143 5965_625
38144 5965_626
38145 5965_627
38146 5965_628
38147 5965_629
38148 5965_630
38149 5965_631
38150 5965_632
38151 5965_633
38152 5965_634
38153 5965_637
38154 5965_638
38155 5965_639
38156 5965_64
38157 5965_640
38158 5965_641
38159 5965_642
38160 5965_643
38161 5965_645
38162 5965_646
38163 5965_647
38164 5965_648
38165 5965_649
38166 5965_65
38167 5965_652
38168 5965_653
38169 5965_654
38170 5965_655
38171 5965_656
38172 5965_657
38173 5965_658
38174 5965_659
38175 5965_660
38176 5965_661
38177 5965_662
38178 5965_663
38179 5965_664
38180 5965_665
38181 5965_666
38182 5965_667
38183 5965_668
38184 5965_669
38185 5965_670
38186 5965_671
38187 5965_672
38188 5965_673
38189 5965_674
38190 5965_675
38191 5965_676
38192 5965_677
38193 5965_678
38194 5965_679
38195 5965_680
38196 5965_681
38197 5965_682
38198 5965_683
38199 5965_684
38200 5965_685
38201 5965_686
38202 5965_687
38203 5965_688
38204 5965_6

38701 6059_395
38702 6059_396
38703 6059_397
38704 6059_4
38705 6059_401
38706 6059_405
38707 6059_406
38708 6059_415
38709 6059_419
38710 6059_420
38711 6059_421
38712 6059_422
38713 6059_428
38714 6059_435
38715 6059_437
38716 6059_438
38717 6059_439
38718 6059_440
38719 6059_441
38720 6059_442
38721 6059_444
38722 6059_453
38723 6059_46
38724 6059_467
38725 6059_468
38726 6059_475
38727 6059_477
38728 6059_478
38729 6059_48
38730 6059_487
38731 6059_488
38732 6059_489
38733 6059_491
38734 6059_495
38735 6059_5
38736 6059_520
38737 6059_522
38738 6059_533
38739 6059_534
38740 6059_557
38741 6059_578
38742 6059_580
38743 6059_581
38744 6059_652
38745 6059_674
38746 6059_7
38747 6059_746
38748 6059_764
38749 6059_775
38750 6059_776
38751 6059_809
38752 6059_81
38753 5951_12
38754 5951_13
38755 5951_14
38756 5951_3
38757 5951_7
38758 5951_9
38759 6106_1000
38760 6106_1001
38761 6106_1002
38762 6106_1003
38763 6106_1004
38764 6106_1005
38765 6106_1006
38766 6106_101
38767 6106_1016
38768

39246 6106_839
39247 6106_84
39248 6106_841
39249 6106_842
39250 6106_843
39251 6106_844
39252 6106_845
39253 6106_846
39254 6106_847
39255 6106_848
39256 6106_85
39257 6106_856
39258 6106_857
39259 6106_858
39260 6106_859
39261 6106_86
39262 6106_861
39263 6106_863
39264 6106_864
39265 6106_867
39266 6106_868
39267 6106_869
39268 6106_87
39269 6106_870
39270 6106_871
39271 6106_872
39272 6106_873
39273 6106_874
39274 6106_875
39275 6106_876
39276 6106_877
39277 6106_878
39278 6106_879
39279 6106_88
39280 6106_884
39281 6106_886
39282 6106_887
39283 6106_888
39284 6106_889
39285 6106_89
39286 6106_890
39287 6106_893
39288 6106_894
39289 6106_895
39290 6106_896
39291 6106_90
39292 6106_909
39293 6106_91
39294 6106_910
39295 6106_912
39296 6106_913
39297 6106_915
39298 6106_917
39299 6106_918
39300 6106_919
39301 6106_92
39302 6106_920
39303 6106_922
39304 6106_932
39305 6106_933
39306 6106_935
39307 6106_936
39308 6106_937
39309 6106_939
39310 6106_942
39311 6106_943
39312 6106_944
3931

39801 6180_181
39802 6180_182
39803 6180_187
39804 6180_188
39805 6180_189
39806 6180_190
39807 6180_191
39808 6180_192
39809 6180_193
39810 6180_195
39811 6180_196
39812 6180_198
39813 6180_199
39814 6180_20
39815 6180_201
39816 6180_202
39817 6180_203
39818 6180_204
39819 6180_205
39820 6180_206
39821 6180_207
39822 6180_208
39823 6180_209
39824 6180_210
39825 6180_211
39826 6180_212
39827 6180_213
39828 6180_214
39829 6180_215
39830 6180_216
39831 6180_217
39832 6180_220
39833 6180_225
39834 6180_227
39835 6180_228
39836 6180_229
39837 6180_236
39838 6180_238
39839 6180_242
39840 6180_251
39841 6180_252
39842 6180_254
39843 6180_261
39844 6180_262
39845 6180_264
39846 6180_266
39847 6180_267
39848 6180_268
39849 6180_270
39850 6180_273
39851 6180_274
39852 6180_275
39853 6180_288
39854 6180_289
39855 6180_291
39856 6180_293
39857 6180_294
39858 6180_295
39859 6180_298
39860 6180_299
39861 6180_300
39862 6180_301
39863 6180_302
39864 6180_303
39865 6180_304
39866 6180_305
39867 6180_

40357 6067_509
40358 6067_51
40359 6067_511
40360 6067_519
40361 6067_52
40362 6067_520
40363 6067_521
40364 6067_522
40365 6067_523
40366 6067_524
40367 6067_525
40368 6067_529
40369 6067_53
40370 6067_530
40371 6067_531
40372 6067_59
40373 6067_6
40374 6067_60
40375 6067_61
40376 6067_62
40377 6067_63
40378 6067_66
40379 6067_68
40380 6067_7
40381 6067_71
40382 6067_72
40383 6067_73
40384 6067_75
40385 6067_77
40386 6067_78
40387 6067_79
40388 6067_8
40389 6067_80
40390 6067_81
40391 6067_82
40392 6067_83
40393 6067_84
40394 6067_85
40395 6067_86
40396 6067_87
40397 6067_89
40398 6067_9
40399 6067_92
40400 6067_93
40401 6067_94
40402 6067_97
40403 6067_98
40404 5939_0
40405 5939_1
40406 5939_100
40407 5939_101
40408 5939_102
40409 5939_103
40410 5939_104
40411 5939_105
40412 5939_106
40413 5939_110
40414 5939_111
40415 5939_112
40416 5939_113
40417 5939_114
40418 5939_116
40419 5939_120
40420 5939_121
40421 5939_122
40422 5939_123
40423 5939_125
40424 5939_126
40425 5939_129
40426 59

In [8]:
search_tolerance = 0.0006
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_75 = group_geo_circles(stop_regions, 75, search_tolerance)
print("{} request circles".format(len(request_circles_75)))

d: 81.15379220334191
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_18

657 6014_453
658 6014_454
659 6014_455
660 6014_456
661 6014_458
662 6014_459
663 6014_46
664 6014_460
665 6014_461
666 6014_462
667 6014_463
668 6014_464
669 6014_465
670 6014_466
671 6014_467
672 6014_468
673 6014_469
674 6014_47
675 6014_470
676 6014_471
677 6014_472
678 6014_473
679 6014_474
680 6014_475
681 6014_476
682 6014_477
683 6014_478
684 6014_479
685 6014_48
686 6014_480
687 6014_481
688 6014_482
689 6014_483
690 6014_486
691 6014_487
692 6014_489
693 6014_49
694 6014_490
695 6014_491
696 6014_492
697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_532
729 6014_533
730 6014_534
731 6014_535
732 6014_536
733 6014_537
734 601

1279 6042_1343
1280 6042_1345
1281 6042_1346
1282 6042_1357
1283 6042_1358
1284 6042_136
1285 6042_1360
1286 6042_1361
1287 6042_1362
1288 6042_1366
1289 6042_1367
1290 6042_1368
1291 6042_1369
1292 6042_1370
1293 6042_1373
1294 6042_1374
1295 6042_1376
1296 6042_139
1297 6042_1390
1298 6042_1395
1299 6042_14
1300 6042_140
1301 6042_141
1302 6042_142
1303 6042_145
1304 6042_152
1305 6042_155
1306 6042_156
1307 6042_157
1308 6042_158
1309 6042_16
1310 6042_161
1311 6042_163
1312 6042_17
1313 6042_171
1314 6042_172
1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
13

1875 5966_674
1876 5966_675
1877 5966_676
1878 5966_677
1879 5966_678
1880 5966_68
1881 5966_682
1882 5966_683
1883 5966_684
1884 5966_688
1885 5966_69
1886 5966_690
1887 5966_691
1888 5966_692
1889 5966_693
1890 5966_695
1891 5966_700
1892 5966_701
1893 5966_706
1894 5966_708
1895 5966_709
1896 5966_71
1897 5966_710
1898 5966_711
1899 5966_713
1900 5966_715
1901 5966_716
1902 5966_717
1903 5966_718
1904 5966_719
1905 5966_72
1906 5966_720
1907 5966_721
1908 5966_731
1909 5966_732
1910 5966_733
1911 5966_736
1912 5966_737
1913 5966_738
1914 5966_739
1915 5966_74
1916 5966_740
1917 5966_742
1918 5966_751
1919 5966_752
1920 5966_754
1921 5966_757
1922 5966_758
1923 5966_759
1924 5966_76
1925 5966_761
1926 5966_763
1927 5966_766
1928 5966_767
1929 5966_768
1930 5966_770
1931 5966_772
1932 5966_773
1933 5966_779
1934 5966_780
1935 5966_782
1936 5966_783
1937 5966_785
1938 5966_787
1939 5966_788
1940 5966_79
1941 5966_796
1942 5966_799
1943 5966_80
1944 5966_800
1945 5966_801
1946 5966_802


2481 5949_133
2482 5949_136
2483 5949_137
2484 5949_138
2485 5949_139
2486 5949_14
2487 5949_140
2488 5949_141
2489 5949_142
2490 5949_143
2491 5949_147
2492 5949_149
2493 5949_150
2494 5949_151
2495 5949_153
2496 5949_154
2497 5949_155
2498 5949_156
2499 5949_157
2500 5949_158
2501 5949_159
2502 5949_161
2503 5949_163
2504 5949_166
2505 5949_167
2506 5949_168
2507 5949_169
2508 5949_17
2509 5949_170
2510 5949_172
2511 5949_175
2512 5949_176
2513 5949_177
2514 5949_18
2515 5949_180
2516 5949_181
2517 5949_182
2518 5949_183
2519 5949_184
2520 5949_185
2521 5949_186
2522 5949_187
2523 5949_188
2524 5949_189
2525 5949_19
2526 5949_190
2527 5949_192
2528 5949_196
2529 5949_199
2530 5949_2
2531 5949_200
2532 5949_203
2533 5949_204
2534 5949_205
2535 5949_206
2536 5949_207
2537 5949_208
2538 5949_21
2539 5949_212
2540 5949_214
2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231

...

38434 6106_438
38435 6106_44
38436 6106_440
38437 6106_442
38438 6106_445
38439 6106_449
38440 6106_45
38441 6106_450
38442 6106_454
38443 6106_455
38444 6106_457
38445 6106_458
38446 6106_459
38447 6106_46
38448 6106_460
38449 6106_467
38450 6106_468
38451 6106_469
38452 6106_47
38453 6106_470
38454 6106_478
38455 6106_48
38456 6106_49
38457 6106_505
38458 6106_506
38459 6106_507
38460 6106_508
38461 6106_511
38462 6106_513
38463 6106_514
38464 6106_515
38465 6106_520
38466 6106_525
38467 6106_529
38468 6106_552
38469 6106_553
38470 6106_554
38471 6106_555
38472 6106_556
38473 6106_557
38474 6106_558
38475 6106_559
38476 6106_560
38477 6106_561
38478 6106_570
38479 6106_572
38480 6106_576
38481 6106_577
38482 6106_578
38483 6106_579
38484 6106_583
38485 6106_584
38486 6106_587
38487 6106_589
38488 6106_595
38489 6106_610
38490 6106_611
38491 6106_614
38492 6106_615
38493 6106_616
38494 6106_617
38495 6106_640
38496 6106_641
38497 6106_642
38498 6106_643
38499 6106_644
38500 6106_648
3

39000 5957_481
39001 5957_488
39002 5957_496
39003 5957_55
39004 5957_7
39005 5957_71
39006 5957_73
39007 5957_79
39008 5957_80
39009 5957_81
39010 5957_88
39011 5957_9
39012 5957_92
39013 5957_96
39014 5957_97
39015 5964_1001
39016 5964_1002
39017 5964_1003
39018 5964_1009
39019 5964_1010
39020 5964_1011
39021 5964_1012
39022 5964_1013
39023 5964_1014
39024 5964_1015
39025 5964_1016
39026 5964_1017
39027 5964_1028
39028 5964_1029
39029 5964_1030
39030 5964_1031
39031 5964_1032
39032 5964_1038
39033 5964_1039
39034 5964_1041
39035 5964_1043
39036 5964_1044
39037 5964_105
39038 5964_1050
39039 5964_1055
39040 5964_1056
39041 5964_106
39042 5964_107
39043 5964_108
39044 5964_109
39045 5964_110
39046 5964_111
39047 5964_112
39048 5964_113
39049 5964_115
39050 5964_116
39051 5964_117
39052 5964_122
39053 5964_123
39054 5964_124
39055 5964_125
39056 5964_129
39057 5964_13
39058 5964_130
39059 5964_131
39060 5964_132
39061 5964_133
39062 5964_134
39063 5964_136
39064 5964_137
39065 5964_138


39552 5964_956
39553 5964_957
39554 5964_963
39555 5964_964
39556 5964_965
39557 5964_967
39558 5964_968
39559 5964_970
39560 5964_971
39561 5964_972
39562 5964_973
39563 5964_974
39564 5964_975
39565 5964_976
39566 5964_977
39567 5964_978
39568 5964_979
39569 5964_980
39570 5964_981
39571 5964_983
39572 5964_984
39573 5964_985
39574 5964_990
39575 5964_992
39576 5964_993
39577 5964_994
39578 5964_995
39579 5964_996
39580 5964_997
39581 5964_998
39582 5964_999
39583 6170_0
39584 6170_1
39585 6170_10
39586 6170_100
39587 6170_101
39588 6170_102
39589 6170_103
39590 6170_104
39591 6170_105
39592 6170_106
39593 6170_108
39594 6170_109
39595 6170_11
39596 6170_110
39597 6170_111
39598 6170_112
39599 6170_113
39600 6170_114
39601 6170_115
39602 6170_117
39603 6170_119
39604 6170_12
39605 6170_120
39606 6170_121
39607 6170_122
39608 6170_123
39609 6170_124
39610 6170_126
39611 6170_127
39612 6170_128
39613 6170_129
39614 6170_130
39615 6170_132
39616 6170_133
39617 6170_134
39618 6170_135
39

40148 6068_231
40149 6068_237
40150 6068_24
40151 6068_247
40152 6068_257
40153 6068_258
40154 6068_259
40155 6068_260
40156 6068_261
40157 6068_262
40158 6068_263
40159 6068_265
40160 6068_266
40161 6068_270
40162 6068_275
40163 6068_276
40164 6068_28
40165 6068_282
40166 6068_29
40167 6068_30
40168 6068_302
40169 6068_307
40170 6068_309
40171 6068_31
40172 6068_310
40173 6068_311
40174 6068_312
40175 6068_313
40176 6068_32
40177 6068_328
40178 6068_35
40179 6068_46
40180 6068_49
40181 6068_53
40182 6068_54
40183 6068_57
40184 6068_58
40185 6068_61
40186 6068_62
40187 6068_63
40188 6068_64
40189 6068_68
40190 6068_69
40191 6068_72
40192 6068_73
40193 6068_74
40194 6068_75
40195 6068_77
40196 6068_78
40197 6068_79
40198 6068_80
40199 6068_81
40200 6068_82
40201 6068_87
40202 6068_88
40203 6068_90
40204 5976_10
40205 5976_1012
40206 5976_1013
40207 5976_1014
40208 5976_1016
40209 5976_1035
40210 5976_1036
40211 5976_1044
40212 5976_1047
40213 5976_1076
40214 5976_1087
40215 5976_109
402

40693 5976_829
40694 5976_830
40695 5976_831
40696 5976_832
40697 5976_835
40698 5976_841
40699 5976_842
40700 5976_843
40701 5976_849
40702 5976_850
40703 5976_851
40704 5976_852
40705 5976_854
40706 5976_855
40707 5976_859
40708 5976_860
40709 5976_862
40710 5976_863
40711 5976_864
40712 5976_865
40713 5976_866
40714 5976_867
40715 5976_868
40716 5976_869
40717 5976_876
40718 5976_883
40719 5976_884
40720 5976_885
40721 5976_886
40722 5976_887
40723 5976_888
40724 5976_889
40725 5976_89
40726 5976_890
40727 5976_891
40728 5976_9
40729 5976_901
40730 5976_902
40731 5976_903
40732 5976_904
40733 5976_919
40734 5976_921
40735 5976_923
40736 5976_924
40737 5976_925
40738 5976_926
40739 5976_927
40740 5976_928
40741 5976_929
40742 5976_937
40743 5976_939
40744 5976_942
40745 5976_943
40746 5976_944
40747 5976_948
40748 5976_954
40749 5976_955
40750 5976_956
40751 5976_957
40752 5976_958
40753 5976_959
40754 5976_960
40755 5976_961
40756 5976_962
40757 5976_964
40758 5976_965
40759 5976_96

In [14]:
search_tolerance = 0.0012
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
#request_circles_100 = group_geo_circles(stop_regions, 100, search_tolerance)
print("{} request circles".format(len(request_circles_100)))

d: 162.30730255778232
8558 request circles


In [9]:
search_tolerance = 0.0015
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_200 = group_geo_circles(stop_regions, 200, search_tolerance)
print("{} request circles".format(len(request_circles_200)))

d: 202.88395204215746
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_1

651 6014_44
652 6014_447
653 6014_448
654 6014_45
655 6014_451
656 6014_452
657 6014_453
658 6014_454
659 6014_455
660 6014_456
661 6014_458
662 6014_459
663 6014_46
664 6014_460
665 6014_461
666 6014_462
667 6014_463
668 6014_464
669 6014_465
670 6014_466
671 6014_467
672 6014_468
673 6014_469
674 6014_47
675 6014_470
676 6014_471
677 6014_472
678 6014_473
679 6014_474
680 6014_475
681 6014_476
682 6014_477
683 6014_478
684 6014_479
685 6014_48
686 6014_480
687 6014_481
688 6014_482
689 6014_483
690 6014_486
691 6014_487
692 6014_489
693 6014_49
694 6014_490
695 6014_491
696 6014_492
697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_

1289 6042_1367
1290 6042_1368
1291 6042_1369
1292 6042_1370
1293 6042_1373
1294 6042_1374
1295 6042_1376
1296 6042_139
1297 6042_1390
1298 6042_1395
1299 6042_14
1300 6042_140
1301 6042_141
1302 6042_142
1303 6042_145
1304 6042_152
1305 6042_155
1306 6042_156
1307 6042_157
1308 6042_158
1309 6042_16
1310 6042_161
1311 6042_163
1312 6042_17
1313 6042_171
1314 6042_172
1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
1350 6042_36
1351 6042_365
1352 6042_366
1353 6042_367
1354 6042_37
1355 6042_39
1356 6042_40
1357 6042_41
1358 6042_415
1359 6042_416
1360 6042_417
13

1887 5966_691
1888 5966_692
1889 5966_693
1890 5966_695
1891 5966_700
1892 5966_701
1893 5966_706
1894 5966_708
1895 5966_709
1896 5966_71
1897 5966_710
1898 5966_711
1899 5966_713
1900 5966_715
1901 5966_716
1902 5966_717
1903 5966_718
1904 5966_719
1905 5966_72
1906 5966_720
1907 5966_721
1908 5966_731
1909 5966_732
1910 5966_733
1911 5966_736
1912 5966_737
1913 5966_738
1914 5966_739
1915 5966_74
1916 5966_740
1917 5966_742
1918 5966_751
1919 5966_752
1920 5966_754
1921 5966_757
1922 5966_758
1923 5966_759
1924 5966_76
1925 5966_761
1926 5966_763
1927 5966_766
1928 5966_767
1929 5966_768
1930 5966_770
1931 5966_772
1932 5966_773
1933 5966_779
1934 5966_780
1935 5966_782
1936 5966_783
1937 5966_785
1938 5966_787
1939 5966_788
1940 5966_79
1941 5966_796
1942 5966_799
1943 5966_80
1944 5966_800
1945 5966_801
1946 5966_802
1947 5966_803
1948 5966_806
1949 5966_809
1950 5966_81
1951 5966_810
1952 5966_811
1953 5966_812
1954 5966_813
1955 5966_814
1956 5966_815
1957 5966_816
1958 5966_817

2483 5949_137
2484 5949_138
2485 5949_139
2486 5949_14
2487 5949_140
2488 5949_141
2489 5949_142
2490 5949_143
2491 5949_147
2492 5949_149
2493 5949_150
2494 5949_151
2495 5949_153
2496 5949_154
2497 5949_155
2498 5949_156
2499 5949_157
2500 5949_158
2501 5949_159
2502 5949_161
2503 5949_163
2504 5949_166
2505 5949_167
2506 5949_168
2507 5949_169
2508 5949_17
2509 5949_170
2510 5949_172
2511 5949_175
2512 5949_176
2513 5949_177
2514 5949_18
2515 5949_180
2516 5949_181
2517 5949_182
2518 5949_183
2519 5949_184
2520 5949_185
2521 5949_186
2522 5949_187
2523 5949_188
2524 5949_189
2525 5949_19
2526 5949_190
2527 5949_192
2528 5949_196
2529 5949_199
2530 5949_2
2531 5949_200
2532 5949_203
2533 5949_204
2534 5949_205
2535 5949_206
2536 5949_207
2537 5949_208
2538 5949_21
2539 5949_212
2540 5949_214
2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231
2553 5949_232
2554 5949_233

...

38428 6106_420
38429 6106_423
38430 6106_424
38431 6106_426
38432 6106_43
38433 6106_437
38434 6106_438
38435 6106_44
38436 6106_440
38437 6106_442
38438 6106_445
38439 6106_449
38440 6106_45
38441 6106_450
38442 6106_454
38443 6106_455
38444 6106_457
38445 6106_458
38446 6106_459
38447 6106_46
38448 6106_460
38449 6106_467
38450 6106_468
38451 6106_469
38452 6106_47
38453 6106_470
38454 6106_478
38455 6106_48
38456 6106_49
38457 6106_505
38458 6106_506
38459 6106_507
38460 6106_508
38461 6106_511
38462 6106_513
38463 6106_514
38464 6106_515
38465 6106_520
38466 6106_525
38467 6106_529
38468 6106_552
38469 6106_553
38470 6106_554
38471 6106_555
38472 6106_556
38473 6106_557
38474 6106_558
38475 6106_559
38476 6106_560
38477 6106_561
38478 6106_570
38479 6106_572
38480 6106_576
38481 6106_577
38482 6106_578
38483 6106_579
38484 6106_583
38485 6106_584
38486 6106_587
38487 6106_589
38488 6106_595
38489 6106_610
38490 6106_611
38491 6106_614
38492 6106_615
38493 6106_616
38494 6106_617
38

39019 5964_1010
39020 5964_1011
39021 5964_1012
39022 5964_1013
39023 5964_1014
39024 5964_1015
39025 5964_1016
39026 5964_1017
39027 5964_1028
39028 5964_1029
39029 5964_1030
39030 5964_1031
39031 5964_1032
39032 5964_1038
39033 5964_1039
39034 5964_1041
39035 5964_1043
39036 5964_1044
39037 5964_105
39038 5964_1050
39039 5964_1055
39040 5964_1056
39041 5964_106
39042 5964_107
39043 5964_108
39044 5964_109
39045 5964_110
39046 5964_111
39047 5964_112
39048 5964_113
39049 5964_115
39050 5964_116
39051 5964_117
39052 5964_122
39053 5964_123
39054 5964_124
39055 5964_125
39056 5964_129
39057 5964_13
39058 5964_130
39059 5964_131
39060 5964_132
39061 5964_133
39062 5964_134
39063 5964_136
39064 5964_137
39065 5964_138
39066 5964_139
39067 5964_14
39068 5964_140
39069 5964_142
39070 5964_143
39071 5964_144
39072 5964_146
39073 5964_147
39074 5964_149
39075 5964_150
39076 5964_151
39077 5964_153
39078 5964_154
39079 5964_155
39080 5964_156
39081 5964_157
39082 5964_158
39083 5964_159
39084 

39585 6170_10
39586 6170_100
39587 6170_101
39588 6170_102
39589 6170_103
39590 6170_104
39591 6170_105
39592 6170_106
39593 6170_108
39594 6170_109
39595 6170_11
39596 6170_110
39597 6170_111
39598 6170_112
39599 6170_113
39600 6170_114
39601 6170_115
39602 6170_117
39603 6170_119
39604 6170_12
39605 6170_120
39606 6170_121
39607 6170_122
39608 6170_123
39609 6170_124
39610 6170_126
39611 6170_127
39612 6170_128
39613 6170_129
39614 6170_130
39615 6170_132
39616 6170_133
39617 6170_134
39618 6170_135
39619 6170_136
39620 6170_138
39621 6170_139
39622 6170_142
39623 6170_145
39624 6170_146
39625 6170_147
39626 6170_148
39627 6170_151
39628 6170_152
39629 6170_153
39630 6170_154
39631 6170_155
39632 6170_156
39633 6170_157
39634 6170_158
39635 6170_160
39636 6170_161
39637 6170_163
39638 6170_166
39639 6170_167
39640 6170_168
39641 6170_169
39642 6170_170
39643 6170_171
39644 6170_174
39645 6170_175
39646 6170_176
39647 6170_178
39648 6170_179
39649 6170_180
39650 6170_181
39651 6170_18

40166 6068_29
40167 6068_30
40168 6068_302
40169 6068_307
40170 6068_309
40171 6068_31
40172 6068_310
40173 6068_311
40174 6068_312
40175 6068_313
40176 6068_32
40177 6068_328
40178 6068_35
40179 6068_46
40180 6068_49
40181 6068_53
40182 6068_54
40183 6068_57
40184 6068_58
40185 6068_61
40186 6068_62
40187 6068_63
40188 6068_64
40189 6068_68
40190 6068_69
40191 6068_72
40192 6068_73
40193 6068_74
40194 6068_75
40195 6068_77
40196 6068_78
40197 6068_79
40198 6068_80
40199 6068_81
40200 6068_82
40201 6068_87
40202 6068_88
40203 6068_90
40204 5976_10
40205 5976_1012
40206 5976_1013
40207 5976_1014
40208 5976_1016
40209 5976_1035
40210 5976_1036
40211 5976_1044
40212 5976_1047
40213 5976_1076
40214 5976_1087
40215 5976_109
40216 5976_11
40217 5976_1105
40218 5976_111
40219 5976_1118
40220 5976_112
40221 5976_1126
40222 5976_1127
40223 5976_1128
40224 5976_1129
40225 5976_1130
40226 5976_1131
40227 5976_1135
40228 5976_1136
40229 5976_1137
40230 5976_1138
40231 5976_1139
40232 5976_1140
402

40730 5976_902
40731 5976_903
40732 5976_904
40733 5976_919
40734 5976_921
40735 5976_923
40736 5976_924
40737 5976_925
40738 5976_926
40739 5976_927
40740 5976_928
40741 5976_929
40742 5976_937
40743 5976_939
40744 5976_942
40745 5976_943
40746 5976_944
40747 5976_948
40748 5976_954
40749 5976_955
40750 5976_956
40751 5976_957
40752 5976_958
40753 5976_959
40754 5976_960
40755 5976_961
40756 5976_962
40757 5976_964
40758 5976_965
40759 5976_969
40760 5976_970
40761 5976_971
40762 5976_972
40763 5976_973
40764 5976_989
40765 5976_998
40766 5976_999
5117 request circles


In [10]:
search_tolerance = 0.0035
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_300 = group_geo_circles(stop_regions, 300, search_tolerance)
print("{} request circles".format(len(request_circles_300)))

d: 473.3931478421088
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_18

683 6014_478
684 6014_479
685 6014_48
686 6014_480
687 6014_481
688 6014_482
689 6014_483
690 6014_486
691 6014_487
692 6014_489
693 6014_49
694 6014_490
695 6014_491
696 6014_492
697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_532
729 6014_533
730 6014_534
731 6014_535
732 6014_536
733 6014_537
734 6014_538
735 6014_539
736 6014_540
737 6014_541
738 6014_542
739 6014_543
740 6014_544
741 6014_545
742 6014_546
743 6014_547
744 6014_548
745 6014_549
746 6014_550
747 6014_551
748 6014_552
749 6014_553
750 6014_554
751 6014_56
752 6014_563
753 6014_564
754 6014_565
755 6014_569
756 6014_57
757 6014_570
758 6014_572
759 6014_573
760 601

1304 6042_152
1305 6042_155
1306 6042_156
1307 6042_157
1308 6042_158
1309 6042_16
1310 6042_161
1311 6042_163
1312 6042_17
1313 6042_171
1314 6042_172
1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
1350 6042_36
1351 6042_365
1352 6042_366
1353 6042_367
1354 6042_37
1355 6042_39
1356 6042_40
1357 6042_41
1358 6042_415
1359 6042_416
1360 6042_417
1361 6042_418
1362 6042_419
1363 6042_42
1364 6042_420
1365 6042_421
1366 6042_422
1367 6042_426
1368 6042_427
1369 6042_428
1370 6042_432
1371 6042_433
1372 6042_434
1373 6042_435
1374 6042_437
1375 6042_438
1376 6042_4

1920 5966_754
1921 5966_757
1922 5966_758
1923 5966_759
1924 5966_76
1925 5966_761
1926 5966_763
1927 5966_766
1928 5966_767
1929 5966_768
1930 5966_770
1931 5966_772
1932 5966_773
1933 5966_779
1934 5966_780
1935 5966_782
1936 5966_783
1937 5966_785
1938 5966_787
1939 5966_788
1940 5966_79
1941 5966_796
1942 5966_799
1943 5966_80
1944 5966_800
1945 5966_801
1946 5966_802
1947 5966_803
1948 5966_806
1949 5966_809
1950 5966_81
1951 5966_810
1952 5966_811
1953 5966_812
1954 5966_813
1955 5966_814
1956 5966_815
1957 5966_816
1958 5966_817
1959 5966_818
1960 5966_822
1961 5966_823
1962 5966_824
1963 5966_825
1964 5966_826
1965 5966_827
1966 5966_830
1967 5966_831
1968 5966_834
1969 5966_835
1970 5966_836
1971 5966_838
1972 5966_839
1973 5966_840
1974 5966_841
1975 5966_846
1976 5966_849
1977 5966_850
1978 5966_855
1979 5966_857
1980 5966_858
1981 5966_859
1982 5966_862
1983 5966_863
1984 5966_867
1985 5966_868
1986 5966_87
1987 5966_870
1988 5966_871
1989 5966_872
1990 5966_873
1991 5966_8

2522 5949_187
2523 5949_188
2524 5949_189
2525 5949_19
2526 5949_190
2527 5949_192
2528 5949_196
2529 5949_199
2530 5949_2
2531 5949_200
2532 5949_203
2533 5949_204
2534 5949_205
2535 5949_206
2536 5949_207
2537 5949_208
2538 5949_21
2539 5949_212
2540 5949_214
2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231
2553 5949_232
2554 5949_233
2555 5949_234
2556 5949_235
2557 5949_236
2558 5949_237
2559 5949_239
2560 5949_241
2561 5949_242
2562 5949_243
2563 5949_244
2564 5949_245
2565 5949_246
2566 5949_247
2567 5949_249
2568 5949_25
2569 5949_255
2570 5949_256
2571 5949_257
2572 5949_259
2573 5949_26
2574 5949_260
2575 5949_261
2576 5949_262
2577 5949_263
2578 5949_264
2579 5949_265
2580 5949_266
2581 5949_267
2582 5949_27
2583 5949_271
2584 5949_272
2585 5949_275
2586 5949_276
2587 5949_278
2588 5949_28
2589 5949_281
2590 5949_282
2591 5949_283
2592 5949_284
2593 5949_285


...

37993 5940_63
37994 5940_630
37995 5940_631
37996 5940_632
37997 5940_633
37998 5940_634
37999 5940_635
38000 5940_636
38001 5940_637
38002 5940_638
38003 5940_639
38004 5940_64
38005 5940_640
38006 5940_641
38007 5940_642
38008 5940_643
38009 5940_644
38010 5940_645
38011 5940_646
38012 5940_647
38013 5940_648
38014 5940_649
38015 5940_65
38016 5940_650
38017 5940_652
38018 5940_653
38019 5940_657
38020 5940_658
38021 5940_659
38022 5940_66
38023 5940_660
38024 5940_661
38025 5940_662
38026 5940_663
38027 5940_666
38028 5940_667
38029 5940_668
38030 5940_669
38031 5940_67
38032 5940_670
38033 5940_671
38034 5940_672
38035 5940_673
38036 5940_674
38037 5940_675
38038 5940_676
38039 5940_68
38040 5940_684
38041 5940_686
38042 5940_688
38043 5940_689
38044 5940_69
38045 5940_691
38046 5940_692
38047 5940_693
38048 5940_694
38049 5940_696
38050 5940_697
38051 5940_698
38052 5940_701
38053 5940_704
38054 5940_706
38055 5940_707
38056 5940_708
38057 5940_709
38058 5940_71
38059 5940_710
380

38538 6106_742
38539 6106_746
38540 6106_747
38541 6106_749
38542 6106_75
38543 6106_750
38544 6106_751
38545 6106_752
38546 6106_753
38547 6106_754
38548 6106_755
38549 6106_756
38550 6106_757
38551 6106_758
38552 6106_759
38553 6106_76
38554 6106_760
38555 6106_761
38556 6106_762
38557 6106_763
38558 6106_766
38559 6106_769
38560 6106_77
38561 6106_774
38562 6106_775
38563 6106_776
38564 6106_777
38565 6106_778
38566 6106_779
38567 6106_78
38568 6106_780
38569 6106_781
38570 6106_782
38571 6106_783
38572 6106_784
38573 6106_789
38574 6106_79
38575 6106_790
38576 6106_791
38577 6106_792
38578 6106_797
38579 6106_798
38580 6106_799
38581 6106_80
38582 6106_800
38583 6106_801
38584 6106_802
38585 6106_809
38586 6106_81
38587 6106_819
38588 6106_82
38589 6106_820
38590 6106_826
38591 6106_827
38592 6106_828
38593 6106_83
38594 6106_832
38595 6106_833
38596 6106_834
38597 6106_836
38598 6106_837
38599 6106_838
38600 6106_839
38601 6106_84
38602 6106_841
38603 6106_842
38604 6106_843
38605

39121 5964_22
39122 5964_223
39123 5964_224
39124 5964_225
39125 5964_226
39126 5964_227
39127 5964_228
39128 5964_230
39129 5964_231
39130 5964_232
39131 5964_233
39132 5964_238
39133 5964_239
39134 5964_240
39135 5964_241
39136 5964_243
39137 5964_244
39138 5964_246
39139 5964_253
39140 5964_254
39141 5964_256
39142 5964_265
39143 5964_266
39144 5964_268
39145 5964_269
39146 5964_27
39147 5964_270
39148 5964_271
39149 5964_272
39150 5964_275
39151 5964_284
39152 5964_285
39153 5964_286
39154 5964_287
39155 5964_288
39156 5964_289
39157 5964_291
39158 5964_292
39159 5964_293
39160 5964_299
39161 5964_300
39162 5964_301
39163 5964_302
39164 5964_303
39165 5964_304
39166 5964_305
39167 5964_306
39168 5964_31
39169 5964_312
39170 5964_313
39171 5964_314
39172 5964_317
39173 5964_32
39174 5964_321
39175 5964_322
39176 5964_323
39177 5964_324
39178 5964_325
39179 5964_327
39180 5964_328
39181 5964_331
39182 5964_335
39183 5964_339
39184 5964_340
39185 5964_341
39186 5964_342
39187 5964_344

39902 6170_592
39903 6170_593
39904 6170_597
39905 6170_6
39906 6170_607
39907 6170_608
39908 6170_609
39909 6170_61
39910 6170_613
39911 6170_614
39912 6170_616
39913 6170_617
39914 6170_618
39915 6170_619
39916 6170_627
39917 6170_632
39918 6170_633
39919 6170_634
39920 6170_639
39921 6170_640
39922 6170_641
39923 6170_642
39924 6170_643
39925 6170_648
39926 6170_65
39927 6170_650
39928 6170_651
39929 6170_652
39930 6170_653
39931 6170_654
39932 6170_655
39933 6170_656
39934 6170_657
39935 6170_66
39936 6170_660
39937 6170_661
39938 6170_662
39939 6170_668
39940 6170_669
39941 6170_67
39942 6170_670
39943 6170_671
39944 6170_672
39945 6170_673
39946 6170_674
39947 6170_676
39948 6170_677
39949 6170_678
39950 6170_68
39951 6170_680
39952 6170_682
39953 6170_685
39954 6170_686
39955 6170_688
39956 6170_69
39957 6170_696
39958 6170_699
39959 6170_7
39960 6170_70
39961 6170_701
39962 6170_702
39963 6170_703
39964 6170_704
39965 6170_708
39966 6170_71
39967 6170_711
39968 6170_714
39969 6

40444 5976_242
40445 5976_25
40446 5976_253
40447 5976_254
40448 5976_255
40449 5976_256
40450 5976_257
40451 5976_258
40452 5976_259
40453 5976_26
40454 5976_260
40455 5976_262
40456 5976_263
40457 5976_265
40458 5976_269
40459 5976_27
40460 5976_270
40461 5976_272
40462 5976_274
40463 5976_28
40464 5976_284
40465 5976_285
40466 5976_286
40467 5976_287
40468 5976_288
40469 5976_289
40470 5976_291
40471 5976_292
40472 5976_293
40473 5976_294
40474 5976_296
40475 5976_299
40476 5976_300
40477 5976_301
40478 5976_302
40479 5976_303
40480 5976_304
40481 5976_305
40482 5976_306
40483 5976_307
40484 5976_314
40485 5976_317
40486 5976_318
40487 5976_319
40488 5976_323
40489 5976_325
40490 5976_326
40491 5976_327
40492 5976_331
40493 5976_340
40494 5976_341
40495 5976_345
40496 5976_346
40497 5976_347
40498 5976_352
40499 5976_353
40500 5976_354
40501 5976_355
40502 5976_356
40503 5976_362
40504 5976_363
40505 5976_367
40506 5976_38
40507 5976_384
40508 5976_385
40509 5976_386
40510 5976_387


In [15]:
search_tolerance = 0.0035
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_400 = group_geo_circles(stop_regions, request_radius=400, search_tolerance=search_tolerance)
print("{} request circles".format(len(request_circles_400)))

d: 473.3931478421088
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_18

683 6014_478
684 6014_479
685 6014_48
686 6014_480
687 6014_481
688 6014_482
689 6014_483
690 6014_486
691 6014_487
692 6014_489
693 6014_49
694 6014_490
695 6014_491
696 6014_492
697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_532
729 6014_533
730 6014_534
731 6014_535
732 6014_536
733 6014_537
734 6014_538
735 6014_539
736 6014_540
737 6014_541
738 6014_542
739 6014_543
740 6014_544
741 6014_545
742 6014_546
743 6014_547
744 6014_548
745 6014_549
746 6014_550
747 6014_551
748 6014_552
749 6014_553
750 6014_554
751 6014_56
752 6014_563
753 6014_564
754 6014_565
755 6014_569
756 6014_57
757 6014_570
758 6014_572
759 6014_573
760 601

1304 6042_152
1305 6042_155
1306 6042_156
1307 6042_157
1308 6042_158
1309 6042_16
1310 6042_161
1311 6042_163
1312 6042_17
1313 6042_171
1314 6042_172
1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
1350 6042_36
1351 6042_365
1352 6042_366
1353 6042_367
1354 6042_37
1355 6042_39
1356 6042_40
1357 6042_41
1358 6042_415
1359 6042_416
1360 6042_417
1361 6042_418
1362 6042_419
1363 6042_42
1364 6042_420
1365 6042_421
1366 6042_422
1367 6042_426
1368 6042_427
1369 6042_428
1370 6042_432
1371 6042_433
1372 6042_434
1373 6042_435
1374 6042_437
1375 6042_438
1376 6042_4

1904 5966_719
1905 5966_72
1906 5966_720
1907 5966_721
1908 5966_731
1909 5966_732
1910 5966_733
1911 5966_736
1912 5966_737
1913 5966_738
1914 5966_739
1915 5966_74
1916 5966_740
1917 5966_742
1918 5966_751
1919 5966_752
1920 5966_754
1921 5966_757
1922 5966_758
1923 5966_759
1924 5966_76
1925 5966_761
1926 5966_763
1927 5966_766
1928 5966_767
1929 5966_768
1930 5966_770
1931 5966_772
1932 5966_773
1933 5966_779
1934 5966_780
1935 5966_782
1936 5966_783
1937 5966_785
1938 5966_787
1939 5966_788
1940 5966_79
1941 5966_796
1942 5966_799
1943 5966_80
1944 5966_800
1945 5966_801
1946 5966_802
1947 5966_803
1948 5966_806
1949 5966_809
1950 5966_81
1951 5966_810
1952 5966_811
1953 5966_812
1954 5966_813
1955 5966_814
1956 5966_815
1957 5966_816
1958 5966_817
1959 5966_818
1960 5966_822
1961 5966_823
1962 5966_824
1963 5966_825
1964 5966_826
1965 5966_827
1966 5966_830
1967 5966_831
1968 5966_834
1969 5966_835
1970 5966_836
1971 5966_838
1972 5966_839
1973 5966_840
1974 5966_841
1975 5966_84

2503 5949_163
2504 5949_166
2505 5949_167
2506 5949_168
2507 5949_169
2508 5949_17
2509 5949_170
2510 5949_172
2511 5949_175
2512 5949_176
2513 5949_177
2514 5949_18
2515 5949_180
2516 5949_181
2517 5949_182
2518 5949_183
2519 5949_184
2520 5949_185
2521 5949_186
2522 5949_187
2523 5949_188
2524 5949_189
2525 5949_19
2526 5949_190
2527 5949_192
2528 5949_196
2529 5949_199
2530 5949_2
2531 5949_200
2532 5949_203
2533 5949_204
2534 5949_205
2535 5949_206
2536 5949_207
2537 5949_208
2538 5949_21
2539 5949_212
2540 5949_214
2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231
2553 5949_232
2554 5949_233
2555 5949_234
2556 5949_235
2557 5949_236
2558 5949_237
2559 5949_239
2560 5949_241
2561 5949_242
2562 5949_243
2563 5949_244
2564 5949_245
2565 5949_246
2566 5949_247
2567 5949_249
2568 5949_25
2569 5949_255
2570 5949_256
2571 5949_257
2572 5949_259
2573 5949_26
2574 5949_260


...

38525 6106_711
38526 6106_712
38527 6106_713
38528 6106_714
38529 6106_715
38530 6106_716
38531 6106_718
38532 6106_719
38533 6106_72
38534 6106_720
38535 6106_73
38536 6106_74
38537 6106_741
38538 6106_742
38539 6106_746
38540 6106_747
38541 6106_749
38542 6106_75
38543 6106_750
38544 6106_751
38545 6106_752
38546 6106_753
38547 6106_754
38548 6106_755
38549 6106_756
38550 6106_757
38551 6106_758
38552 6106_759
38553 6106_76
38554 6106_760
38555 6106_761
38556 6106_762
38557 6106_763
38558 6106_766
38559 6106_769
38560 6106_77
38561 6106_774
38562 6106_775
38563 6106_776
38564 6106_777
38565 6106_778
38566 6106_779
38567 6106_78
38568 6106_780
38569 6106_781
38570 6106_782
38571 6106_783
38572 6106_784
38573 6106_789
38574 6106_79
38575 6106_790
38576 6106_791
38577 6106_792
38578 6106_797
38579 6106_798
38580 6106_799
38581 6106_80
38582 6106_800
38583 6106_801
38584 6106_802
38585 6106_809
38586 6106_81
38587 6106_819
38588 6106_82
38589 6106_820
38590 6106_826
38591 6106_827
38592 

39085 5964_163
39086 5964_164
39087 5964_165
39088 5964_166
39089 5964_167
39090 5964_168
39091 5964_169
39092 5964_17
39093 5964_170
39094 5964_171
39095 5964_172
39096 5964_173
39097 5964_176
39098 5964_179
39099 5964_18
39100 5964_184
39101 5964_185
39102 5964_186
39103 5964_187
39104 5964_188
39105 5964_189
39106 5964_19
39107 5964_196
39108 5964_197
39109 5964_198
39110 5964_199
39111 5964_20
39112 5964_200
39113 5964_201
39114 5964_202
39115 5964_203
39116 5964_213
39117 5964_215
39118 5964_216
39119 5964_217
39120 5964_219
39121 5964_22
39122 5964_223
39123 5964_224
39124 5964_225
39125 5964_226
39126 5964_227
39127 5964_228
39128 5964_230
39129 5964_231
39130 5964_232
39131 5964_233
39132 5964_238
39133 5964_239
39134 5964_240
39135 5964_241
39136 5964_243
39137 5964_244
39138 5964_246
39139 5964_253
39140 5964_254
39141 5964_256
39142 5964_265
39143 5964_266
39144 5964_268
39145 5964_269
39146 5964_27
39147 5964_270
39148 5964_271
39149 5964_272
39150 5964_275
39151 5964_284
3

39651 6170_182
39652 6170_183
39653 6170_184
39654 6170_185
39655 6170_186
39656 6170_188
39657 6170_192
39658 6170_193
39659 6170_194
39660 6170_196
39661 6170_2
39662 6170_20
39663 6170_200
39664 6170_201
39665 6170_202
39666 6170_208
39667 6170_209
39668 6170_21
39669 6170_210
39670 6170_211
39671 6170_212
39672 6170_213
39673 6170_214
39674 6170_217
39675 6170_218
39676 6170_219
39677 6170_22
39678 6170_221
39679 6170_23
39680 6170_230
39681 6170_231
39682 6170_232
39683 6170_233
39684 6170_238
39685 6170_239
39686 6170_24
39687 6170_240
39688 6170_25
39689 6170_253
39690 6170_254
39691 6170_257
39692 6170_258
39693 6170_26
39694 6170_263
39695 6170_266
39696 6170_267
39697 6170_268
39698 6170_27
39699 6170_270
39700 6170_272
39701 6170_273
39702 6170_274
39703 6170_277
39704 6170_278
39705 6170_28
39706 6170_280
39707 6170_281
39708 6170_282
39709 6170_287
39710 6170_289
39711 6170_29
39712 6170_290
39713 6170_291
39714 6170_292
39715 6170_293
39716 6170_294
39717 6170_295
39718 6

40222 5976_1127
40223 5976_1128
40224 5976_1129
40225 5976_1130
40226 5976_1131
40227 5976_1135
40228 5976_1136
40229 5976_1137
40230 5976_1138
40231 5976_1139
40232 5976_1140
40233 5976_1142
40234 5976_1143
40235 5976_1145
40236 5976_1146
40237 5976_1147
40238 5976_1148
40239 5976_1160
40240 5976_1161
40241 5976_118
40242 5976_1180
40243 5976_1181
40244 5976_1182
40245 5976_1183
40246 5976_1184
40247 5976_1185
40248 5976_1186
40249 5976_1187
40250 5976_1188
40251 5976_1190
40252 5976_120
40253 5976_1202
40254 5976_1204
40255 5976_1205
40256 5976_1206
40257 5976_1208
40258 5976_121
40259 5976_1214
40260 5976_1215
40261 5976_1216
40262 5976_1217
40263 5976_1218
40264 5976_1219
40265 5976_122
40266 5976_1220
40267 5976_1221
40268 5976_1227
40269 5976_1228
40270 5976_1229
40271 5976_1232
40272 5976_1241
40273 5976_1242
40274 5976_1243
40275 5976_1247
40276 5976_1248
40277 5976_1249
40278 5976_1250
40279 5976_1263
40280 5976_1264
40281 5976_1266
40282 5976_1271
40283 5976_1273
40284 5976_1

3186 request circles


In [16]:
search_tolerance = 0.0070
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_500 = group_geo_circles(stop_regions, request_radius=500, search_tolerance=search_tolerance)
print("{} request circles".format(len(request_circles_500)))

d: 946.7767043702323
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_18

663 6014_46
664 6014_460
665 6014_461
666 6014_462
667 6014_463
668 6014_464
669 6014_465
670 6014_466
671 6014_467
672 6014_468
673 6014_469
674 6014_47
675 6014_470
676 6014_471
677 6014_472
678 6014_473
679 6014_474
680 6014_475
681 6014_476
682 6014_477
683 6014_478
684 6014_479
685 6014_48
686 6014_480
687 6014_481
688 6014_482
689 6014_483
690 6014_486
691 6014_487
692 6014_489
693 6014_49
694 6014_490
695 6014_491
696 6014_492
697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_532
729 6014_533
730 6014_534
731 6014_535
732 6014_536
733 6014_537
734 6014_538
735 6014_539
736 6014_540
737 6014_541
738 6014_542
739 6014_543
740 601

1297 6042_1390
1298 6042_1395
1299 6042_14
1300 6042_140
1301 6042_141
1302 6042_142
1303 6042_145
1304 6042_152
1305 6042_155
1306 6042_156
1307 6042_157
1308 6042_158
1309 6042_16
1310 6042_161
1311 6042_163
1312 6042_17
1313 6042_171
1314 6042_172
1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
1350 6042_36
1351 6042_365
1352 6042_366
1353 6042_367
1354 6042_37
1355 6042_39
1356 6042_40
1357 6042_41
1358 6042_415
1359 6042_416
1360 6042_417
1361 6042_418
1362 6042_419
1363 6042_42
1364 6042_420
1365 6042_421
1366 6042_422
1367 6042_426
1368 6042_427
1369 6042_

1891 5966_700
1892 5966_701
1893 5966_706
1894 5966_708
1895 5966_709
1896 5966_71
1897 5966_710
1898 5966_711
1899 5966_713
1900 5966_715
1901 5966_716
1902 5966_717
1903 5966_718
1904 5966_719
1905 5966_72
1906 5966_720
1907 5966_721
1908 5966_731
1909 5966_732
1910 5966_733
1911 5966_736
1912 5966_737
1913 5966_738
1914 5966_739
1915 5966_74
1916 5966_740
1917 5966_742
1918 5966_751
1919 5966_752
1920 5966_754
1921 5966_757
1922 5966_758
1923 5966_759
1924 5966_76
1925 5966_761
1926 5966_763
1927 5966_766
1928 5966_767
1929 5966_768
1930 5966_770
1931 5966_772
1932 5966_773
1933 5966_779
1934 5966_780
1935 5966_782
1936 5966_783
1937 5966_785
1938 5966_787
1939 5966_788
1940 5966_79
1941 5966_796
1942 5966_799
1943 5966_80
1944 5966_800
1945 5966_801
1946 5966_802
1947 5966_803
1948 5966_806
1949 5966_809
1950 5966_81
1951 5966_810
1952 5966_811
1953 5966_812
1954 5966_813
1955 5966_814
1956 5966_815
1957 5966_816
1958 5966_817
1959 5966_818
1960 5966_822
1961 5966_823
1962 5966_824

2487 5949_140
2488 5949_141
2489 5949_142
2490 5949_143
2491 5949_147
2492 5949_149
2493 5949_150
2494 5949_151
2495 5949_153
2496 5949_154
2497 5949_155
2498 5949_156
2499 5949_157
2500 5949_158
2501 5949_159
2502 5949_161
2503 5949_163
2504 5949_166
2505 5949_167
2506 5949_168
2507 5949_169
2508 5949_17
2509 5949_170
2510 5949_172
2511 5949_175
2512 5949_176
2513 5949_177
2514 5949_18
2515 5949_180
2516 5949_181
2517 5949_182
2518 5949_183
2519 5949_184
2520 5949_185
2521 5949_186
2522 5949_187
2523 5949_188
2524 5949_189
2525 5949_19
2526 5949_190
2527 5949_192
2528 5949_196
2529 5949_199
2530 5949_2
2531 5949_200
2532 5949_203
2533 5949_204
2534 5949_205
2535 5949_206
2536 5949_207
2537 5949_208
2538 5949_21
2539 5949_212
2540 5949_214
2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231
2553 5949_232
2554 5949_233
2555 5949_234
2556 5949_235
2557 5949_236
2558 5949_23

...

38462 6106_513
38463 6106_514
38464 6106_515
38465 6106_520
38466 6106_525
38467 6106_529
38468 6106_552
38469 6106_553
38470 6106_554
38471 6106_555
38472 6106_556
38473 6106_557
38474 6106_558
38475 6106_559
38476 6106_560
38477 6106_561
38478 6106_570
38479 6106_572
38480 6106_576
38481 6106_577
38482 6106_578
38483 6106_579
38484 6106_583
38485 6106_584
38486 6106_587
38487 6106_589
38488 6106_595
38489 6106_610
38490 6106_611
38491 6106_614
38492 6106_615
38493 6106_616
38494 6106_617
38495 6106_640
38496 6106_641
38497 6106_642
38498 6106_643
38499 6106_644
38500 6106_648
38501 6106_652
38502 6106_653
38503 6106_654
38504 6106_655
38505 6106_656
38506 6106_657
38507 6106_660
38508 6106_667
38509 6106_668
38510 6106_669
38511 6106_670
38512 6106_671
38513 6106_673
38514 6106_675
38515 6106_683
38516 6106_69
38517 6106_692
38518 6106_694
38519 6106_695
38520 6106_696
38521 6106_697
38522 6106_704
38523 6106_709
38524 6106_71
38525 6106_711
38526 6106_712
38527 6106_713
38528 6106_7

39029 5964_1030
39030 5964_1031
39031 5964_1032
39032 5964_1038
39033 5964_1039
39034 5964_1041
39035 5964_1043
39036 5964_1044
39037 5964_105
39038 5964_1050
39039 5964_1055
39040 5964_1056
39041 5964_106
39042 5964_107
39043 5964_108
39044 5964_109
39045 5964_110
39046 5964_111
39047 5964_112
39048 5964_113
39049 5964_115
39050 5964_116
39051 5964_117
39052 5964_122
39053 5964_123
39054 5964_124
39055 5964_125
39056 5964_129
39057 5964_13
39058 5964_130
39059 5964_131
39060 5964_132
39061 5964_133
39062 5964_134
39063 5964_136
39064 5964_137
39065 5964_138
39066 5964_139
39067 5964_14
39068 5964_140
39069 5964_142
39070 5964_143
39071 5964_144
39072 5964_146
39073 5964_147
39074 5964_149
39075 5964_150
39076 5964_151
39077 5964_153
39078 5964_154
39079 5964_155
39080 5964_156
39081 5964_157
39082 5964_158
39083 5964_159
39084 5964_160
39085 5964_163
39086 5964_164
39087 5964_165
39088 5964_166
39089 5964_167
39090 5964_168
39091 5964_169
39092 5964_17
39093 5964_170
39094 5964_171
39

39585 6170_10
39586 6170_100
39587 6170_101
39588 6170_102
39589 6170_103
39590 6170_104
39591 6170_105
39592 6170_106
39593 6170_108
39594 6170_109
39595 6170_11
39596 6170_110
39597 6170_111
39598 6170_112
39599 6170_113
39600 6170_114
39601 6170_115
39602 6170_117
39603 6170_119
39604 6170_12
39605 6170_120
39606 6170_121
39607 6170_122
39608 6170_123
39609 6170_124
39610 6170_126
39611 6170_127
39612 6170_128
39613 6170_129
39614 6170_130
39615 6170_132
39616 6170_133
39617 6170_134
39618 6170_135
39619 6170_136
39620 6170_138
39621 6170_139
39622 6170_142
39623 6170_145
39624 6170_146
39625 6170_147
39626 6170_148
39627 6170_151
39628 6170_152
39629 6170_153
39630 6170_154
39631 6170_155
39632 6170_156
39633 6170_157
39634 6170_158
39635 6170_160
39636 6170_161
39637 6170_163
39638 6170_166
39639 6170_167
39640 6170_168
39641 6170_169
39642 6170_170
39643 6170_171
39644 6170_174
39645 6170_175
39646 6170_176
39647 6170_178
39648 6170_179
39649 6170_180
39650 6170_181
39651 6170_18

40228 5976_1136
40229 5976_1137
40230 5976_1138
40231 5976_1139
40232 5976_1140
40233 5976_1142
40234 5976_1143
40235 5976_1145
40236 5976_1146
40237 5976_1147
40238 5976_1148
40239 5976_1160
40240 5976_1161
40241 5976_118
40242 5976_1180
40243 5976_1181
40244 5976_1182
40245 5976_1183
40246 5976_1184
40247 5976_1185
40248 5976_1186
40249 5976_1187
40250 5976_1188
40251 5976_1190
40252 5976_120
40253 5976_1202
40254 5976_1204
40255 5976_1205
40256 5976_1206
40257 5976_1208
40258 5976_121
40259 5976_1214
40260 5976_1215
40261 5976_1216
40262 5976_1217
40263 5976_1218
40264 5976_1219
40265 5976_122
40266 5976_1220
40267 5976_1221
40268 5976_1227
40269 5976_1228
40270 5976_1229
40271 5976_1232
40272 5976_1241
40273 5976_1242
40274 5976_1243
40275 5976_1247
40276 5976_1248
40277 5976_1249
40278 5976_1250
40279 5976_1263
40280 5976_1264
40281 5976_1266
40282 5976_1271
40283 5976_1273
40284 5976_1274
40285 5976_1275
40286 5976_1276
40287 5976_1277
40288 5976_1292
40289 5976_1293
40290 5976_1

2599 request circles


In [17]:
search_tolerance = 0.0049
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_600 = group_geo_circles(stop_regions, 600, search_tolerance)
print("{} request circles".format(len(request_circles_600)))

d: 662.7477214555518
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_18

663 6014_46
664 6014_460
665 6014_461
666 6014_462
667 6014_463
668 6014_464
669 6014_465
670 6014_466
671 6014_467
672 6014_468
673 6014_469
674 6014_47
675 6014_470
676 6014_471
677 6014_472
678 6014_473
679 6014_474
680 6014_475
681 6014_476
682 6014_477
683 6014_478
684 6014_479
685 6014_48
686 6014_480
687 6014_481
688 6014_482
689 6014_483
690 6014_486
691 6014_487
692 6014_489
693 6014_49
694 6014_490
695 6014_491
696 6014_492
697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_532
729 6014_533
730 6014_534
731 6014_535
732 6014_536
733 6014_537
734 6014_538
735 6014_539
736 6014_540
737 6014_541
738 6014_542
739 6014_543
740 601

1297 6042_1390
1298 6042_1395
1299 6042_14
1300 6042_140
1301 6042_141
1302 6042_142
1303 6042_145
1304 6042_152
1305 6042_155
1306 6042_156
1307 6042_157
1308 6042_158
1309 6042_16
1310 6042_161
1311 6042_163
1312 6042_17
1313 6042_171
1314 6042_172
1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
1350 6042_36
1351 6042_365
1352 6042_366
1353 6042_367
1354 6042_37
1355 6042_39
1356 6042_40
1357 6042_41
1358 6042_415
1359 6042_416
1360 6042_417
1361 6042_418
1362 6042_419
1363 6042_42
1364 6042_420
1365 6042_421
1366 6042_422
1367 6042_426
1368 6042_427
1369 6042_

1913 5966_738
1914 5966_739
1915 5966_74
1916 5966_740
1917 5966_742
1918 5966_751
1919 5966_752
1920 5966_754
1921 5966_757
1922 5966_758
1923 5966_759
1924 5966_76
1925 5966_761
1926 5966_763
1927 5966_766
1928 5966_767
1929 5966_768
1930 5966_770
1931 5966_772
1932 5966_773
1933 5966_779
1934 5966_780
1935 5966_782
1936 5966_783
1937 5966_785
1938 5966_787
1939 5966_788
1940 5966_79
1941 5966_796
1942 5966_799
1943 5966_80
1944 5966_800
1945 5966_801
1946 5966_802
1947 5966_803
1948 5966_806
1949 5966_809
1950 5966_81
1951 5966_810
1952 5966_811
1953 5966_812
1954 5966_813
1955 5966_814
1956 5966_815
1957 5966_816
1958 5966_817
1959 5966_818
1960 5966_822
1961 5966_823
1962 5966_824
1963 5966_825
1964 5966_826
1965 5966_827
1966 5966_830
1967 5966_831
1968 5966_834
1969 5966_835
1970 5966_836
1971 5966_838
1972 5966_839
1973 5966_840
1974 5966_841
1975 5966_846
1976 5966_849
1977 5966_850
1978 5966_855
1979 5966_857
1980 5966_858
1981 5966_859
1982 5966_862
1983 5966_863
1984 5966_8

2516 5949_181
2517 5949_182
2518 5949_183
2519 5949_184
2520 5949_185
2521 5949_186
2522 5949_187
2523 5949_188
2524 5949_189
2525 5949_19
2526 5949_190
2527 5949_192
2528 5949_196
2529 5949_199
2530 5949_2
2531 5949_200
2532 5949_203
2533 5949_204
2534 5949_205
2535 5949_206
2536 5949_207
2537 5949_208
2538 5949_21
2539 5949_212
2540 5949_214
2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231
2553 5949_232
2554 5949_233
2555 5949_234
2556 5949_235
2557 5949_236
2558 5949_237
2559 5949_239
2560 5949_241
2561 5949_242
2562 5949_243
2563 5949_244
2564 5949_245
2565 5949_246
2566 5949_247
2567 5949_249
2568 5949_25
2569 5949_255
2570 5949_256
2571 5949_257
2572 5949_259
2573 5949_26
2574 5949_260
2575 5949_261
2576 5949_262
2577 5949_263
2578 5949_264
2579 5949_265
2580 5949_266
2581 5949_267
2582 5949_27
2583 5949_271
2584 5949_272
2585 5949_275
2586 5949_276
2587 5949_278

...

37856 5940_403
37857 5940_405
37858 5940_406
37859 5940_407
37860 5940_408
37861 5940_409
37862 5940_41
37863 5940_412
37864 5940_414
37865 5940_415
37866 5940_416
37867 5940_417
37868 5940_418
37869 5940_419
37870 5940_428
37871 5940_429
37872 5940_430
37873 5940_431
37874 5940_432
37875 5940_433
37876 5940_438
37877 5940_439
37878 5940_441
37879 5940_443
37880 5940_444
37881 5940_445
37882 5940_448
37883 5940_449
37884 5940_450
37885 5940_451
37886 5940_452
37887 5940_453
37888 5940_46
37889 5940_47
37890 5940_471
37891 5940_472
37892 5940_483
37893 5940_490
37894 5940_491
37895 5940_492
37896 5940_493
37897 5940_494
37898 5940_495
37899 5940_496
37900 5940_497
37901 5940_498
37902 5940_499
37903 5940_500
37904 5940_503
37905 5940_504
37906 5940_505
37907 5940_506
37908 5940_507
37909 5940_508
37910 5940_509
37911 5940_510
37912 5940_511
37913 5940_512
37914 5940_52
37915 5940_521
37916 5940_524
37917 5940_526
37918 5940_53
37919 5940_532
37920 5940_533
37921 5940_54
37922 5940_543
3

38525 6106_711
38526 6106_712
38527 6106_713
38528 6106_714
38529 6106_715
38530 6106_716
38531 6106_718
38532 6106_719
38533 6106_72
38534 6106_720
38535 6106_73
38536 6106_74
38537 6106_741
38538 6106_742
38539 6106_746
38540 6106_747
38541 6106_749
38542 6106_75
38543 6106_750
38544 6106_751
38545 6106_752
38546 6106_753
38547 6106_754
38548 6106_755
38549 6106_756
38550 6106_757
38551 6106_758
38552 6106_759
38553 6106_76
38554 6106_760
38555 6106_761
38556 6106_762
38557 6106_763
38558 6106_766
38559 6106_769
38560 6106_77
38561 6106_774
38562 6106_775
38563 6106_776
38564 6106_777
38565 6106_778
38566 6106_779
38567 6106_78
38568 6106_780
38569 6106_781
38570 6106_782
38571 6106_783
38572 6106_784
38573 6106_789
38574 6106_79
38575 6106_790
38576 6106_791
38577 6106_792
38578 6106_797
38579 6106_798
38580 6106_799
38581 6106_80
38582 6106_800
38583 6106_801
38584 6106_802
38585 6106_809
38586 6106_81
38587 6106_819
38588 6106_82
38589 6106_820
38590 6106_826
38591 6106_827
38592 

39085 5964_163
39086 5964_164
39087 5964_165
39088 5964_166
39089 5964_167
39090 5964_168
39091 5964_169
39092 5964_17
39093 5964_170
39094 5964_171
39095 5964_172
39096 5964_173
39097 5964_176
39098 5964_179
39099 5964_18
39100 5964_184
39101 5964_185
39102 5964_186
39103 5964_187
39104 5964_188
39105 5964_189
39106 5964_19
39107 5964_196
39108 5964_197
39109 5964_198
39110 5964_199
39111 5964_20
39112 5964_200
39113 5964_201
39114 5964_202
39115 5964_203
39116 5964_213
39117 5964_215
39118 5964_216
39119 5964_217
39120 5964_219
39121 5964_22
39122 5964_223
39123 5964_224
39124 5964_225
39125 5964_226
39126 5964_227
39127 5964_228
39128 5964_230
39129 5964_231
39130 5964_232
39131 5964_233
39132 5964_238
39133 5964_239
39134 5964_240
39135 5964_241
39136 5964_243
39137 5964_244
39138 5964_246
39139 5964_253
39140 5964_254
39141 5964_256
39142 5964_265
39143 5964_266
39144 5964_268
39145 5964_269
39146 5964_27
39147 5964_270
39148 5964_271
39149 5964_272
39150 5964_275
39151 5964_284
3

39654 6170_185
39655 6170_186
39656 6170_188
39657 6170_192
39658 6170_193
39659 6170_194
39660 6170_196
39661 6170_2
39662 6170_20
39663 6170_200
39664 6170_201
39665 6170_202
39666 6170_208
39667 6170_209
39668 6170_21
39669 6170_210
39670 6170_211
39671 6170_212
39672 6170_213
39673 6170_214
39674 6170_217
39675 6170_218
39676 6170_219
39677 6170_22
39678 6170_221
39679 6170_23
39680 6170_230
39681 6170_231
39682 6170_232
39683 6170_233
39684 6170_238
39685 6170_239
39686 6170_24
39687 6170_240
39688 6170_25
39689 6170_253
39690 6170_254
39691 6170_257
39692 6170_258
39693 6170_26
39694 6170_263
39695 6170_266
39696 6170_267
39697 6170_268
39698 6170_27
39699 6170_270
39700 6170_272
39701 6170_273
39702 6170_274
39703 6170_277
39704 6170_278
39705 6170_28
39706 6170_280
39707 6170_281
39708 6170_282
39709 6170_287
39710 6170_289
39711 6170_29
39712 6170_290
39713 6170_291
39714 6170_292
39715 6170_293
39716 6170_294
39717 6170_295
39718 6170_296
39719 6170_297
39720 6170_298
39721 6

40252 5976_120
40253 5976_1202
40254 5976_1204
40255 5976_1205
40256 5976_1206
40257 5976_1208
40258 5976_121
40259 5976_1214
40260 5976_1215
40261 5976_1216
40262 5976_1217
40263 5976_1218
40264 5976_1219
40265 5976_122
40266 5976_1220
40267 5976_1221
40268 5976_1227
40269 5976_1228
40270 5976_1229
40271 5976_1232
40272 5976_1241
40273 5976_1242
40274 5976_1243
40275 5976_1247
40276 5976_1248
40277 5976_1249
40278 5976_1250
40279 5976_1263
40280 5976_1264
40281 5976_1266
40282 5976_1271
40283 5976_1273
40284 5976_1274
40285 5976_1275
40286 5976_1276
40287 5976_1277
40288 5976_1292
40289 5976_1293
40290 5976_1295
40291 5976_1296
40292 5976_1298
40293 5976_1299
40294 5976_1300
40295 5976_1301
40296 5976_1309
40297 5976_1310
40298 5976_1314
40299 5976_1333
40300 5976_1334
40301 5976_1335
40302 5976_1336
40303 5976_1337
40304 5976_1347
40305 5976_1348
40306 5976_1349
40307 5976_1350
40308 5976_1351
40309 5976_1352
40310 5976_1389
40311 5976_1390
40312 5976_1391
40313 5976_1392
40314 5976_

In [18]:
search_tolerance = 0.0070
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_700 = group_geo_circles(stop_regions, request_radius=700, search_tolerance=search_tolerance)
print("{} request circles".format(len(request_circles_700)))

d: 946.7767043702323
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_18

697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_532
729 6014_533
730 6014_534
731 6014_535
732 6014_536
733 6014_537
734 6014_538
735 6014_539
736 6014_540
737 6014_541
738 6014_542
739 6014_543
740 6014_544
741 6014_545
742 6014_546
743 6014_547
744 6014_548
745 6014_549
746 6014_550
747 6014_551
748 6014_552
749 6014_553
750 6014_554
751 6014_56
752 6014_563
753 6014_564
754 6014_565
755 6014_569
756 6014_57
757 6014_570
758 6014_572
759 6014_573
760 6014_574
761 6014_575
762 6014_576
763 6014_577
764 6014_578
765 6014_579
766 6014_58
767 6014_580
768 6014_581
769 6014_582
770 6014_583
771 6014_584
772 6014_585
773 6014_586
774 60

1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
1350 6042_36
1351 6042_365
1352 6042_366
1353 6042_367
1354 6042_37
1355 6042_39
1356 6042_40
1357 6042_41
1358 6042_415
1359 6042_416
1360 6042_417
1361 6042_418
1362 6042_419
1363 6042_42
1364 6042_420
1365 6042_421
1366 6042_422
1367 6042_426
1368 6042_427
1369 6042_428
1370 6042_432
1371 6042_433
1372 6042_434
1373 6042_435
1374 6042_437
1375 6042_438
1376 6042_44
1377 6042_447
1378 6042_448
1379 6042_449
1380 6042_450
1381 6042_451
1382 6042_452
1383 6042_475
1384 6042_476
1385 6042_477
1386 6042_478
1387 6042_

1946 5966_802
1947 5966_803
1948 5966_806
1949 5966_809
1950 5966_81
1951 5966_810
1952 5966_811
1953 5966_812
1954 5966_813
1955 5966_814
1956 5966_815
1957 5966_816
1958 5966_817
1959 5966_818
1960 5966_822
1961 5966_823
1962 5966_824
1963 5966_825
1964 5966_826
1965 5966_827
1966 5966_830
1967 5966_831
1968 5966_834
1969 5966_835
1970 5966_836
1971 5966_838
1972 5966_839
1973 5966_840
1974 5966_841
1975 5966_846
1976 5966_849
1977 5966_850
1978 5966_855
1979 5966_857
1980 5966_858
1981 5966_859
1982 5966_862
1983 5966_863
1984 5966_867
1985 5966_868
1986 5966_87
1987 5966_870
1988 5966_871
1989 5966_872
1990 5966_873
1991 5966_874
1992 5966_877
1993 5966_879
1994 5966_88
1995 5966_880
1996 5966_881
1997 5966_882
1998 5966_885
1999 5966_886
2000 5966_887
2001 5966_889
2002 5966_890
2003 5966_891
2004 5966_892
2005 5966_896
2006 5966_897
2007 5966_899
2008 5966_90
2009 5966_901
2010 5966_906
2011 5966_907
2012 5966_909
2013 5966_91
2014 5966_910
2015 5966_913
2016 5966_914
2017 5966_9

2540 5949_214
2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231
2553 5949_232
2554 5949_233
2555 5949_234
2556 5949_235
2557 5949_236
2558 5949_237
2559 5949_239
2560 5949_241
2561 5949_242
2562 5949_243
2563 5949_244
2564 5949_245
2565 5949_246
2566 5949_247
2567 5949_249
2568 5949_25
2569 5949_255
2570 5949_256
2571 5949_257
2572 5949_259
2573 5949_26
2574 5949_260
2575 5949_261
2576 5949_262
2577 5949_263
2578 5949_264
2579 5949_265
2580 5949_266
2581 5949_267
2582 5949_27
2583 5949_271
2584 5949_272
2585 5949_275
2586 5949_276
2587 5949_278
2588 5949_28
2589 5949_281
2590 5949_282
2591 5949_283
2592 5949_284
2593 5949_285
2594 5949_286
2595 5949_287
2596 5949_288
2597 5949_289
2598 5949_296
2599 5949_297
2600 5949_298
2601 5949_299
2602 5949_30
2603 5949_300
2604 5949_301
2605 5949_303
2606 5949_31
2607 5949_32
2608 5949_320
2609 5949_321
2610 5949_322
2611 5949_323

...

37796 5940_309
37797 5940_31
37798 5940_310
37799 5940_311
37800 5940_312
37801 5940_313
37802 5940_315
37803 5940_316
37804 5940_317
37805 5940_318
37806 5940_319
37807 5940_32
37808 5940_320
37809 5940_321
37810 5940_322
37811 5940_33
37812 5940_330
37813 5940_331
37814 5940_336
37815 5940_34
37816 5940_340
37817 5940_341
37818 5940_343
37819 5940_344
37820 5940_345
37821 5940_346
37822 5940_348
37823 5940_349
37824 5940_35
37825 5940_350
37826 5940_351
37827 5940_358
37828 5940_359
37829 5940_360
37830 5940_361
37831 5940_365
37832 5940_367
37833 5940_368
37834 5940_369
37835 5940_37
37836 5940_370
37837 5940_373
37838 5940_374
37839 5940_375
37840 5940_376
37841 5940_377
37842 5940_38
37843 5940_386
37844 5940_387
37845 5940_39
37846 5940_391
37847 5940_392
37848 5940_393
37849 5940_394
37850 5940_395
37851 5940_396
37852 5940_40
37853 5940_400
37854 5940_401
37855 5940_402
37856 5940_403
37857 5940_405
37858 5940_406
37859 5940_407
37860 5940_408
37861 5940_409
37862 5940_41
37863

38525 6106_711
38526 6106_712
38527 6106_713
38528 6106_714
38529 6106_715
38530 6106_716
38531 6106_718
38532 6106_719
38533 6106_72
38534 6106_720
38535 6106_73
38536 6106_74
38537 6106_741
38538 6106_742
38539 6106_746
38540 6106_747
38541 6106_749
38542 6106_75
38543 6106_750
38544 6106_751
38545 6106_752
38546 6106_753
38547 6106_754
38548 6106_755
38549 6106_756
38550 6106_757
38551 6106_758
38552 6106_759
38553 6106_76
38554 6106_760
38555 6106_761
38556 6106_762
38557 6106_763
38558 6106_766
38559 6106_769
38560 6106_77
38561 6106_774
38562 6106_775
38563 6106_776
38564 6106_777
38565 6106_778
38566 6106_779
38567 6106_78
38568 6106_780
38569 6106_781
38570 6106_782
38571 6106_783
38572 6106_784
38573 6106_789
38574 6106_79
38575 6106_790
38576 6106_791
38577 6106_792
38578 6106_797
38579 6106_798
38580 6106_799
38581 6106_80
38582 6106_800
38583 6106_801
38584 6106_802
38585 6106_809
38586 6106_81
38587 6106_819
38588 6106_82
38589 6106_820
38590 6106_826
38591 6106_827
38592 

39089 5964_167
39090 5964_168
39091 5964_169
39092 5964_17
39093 5964_170
39094 5964_171
39095 5964_172
39096 5964_173
39097 5964_176
39098 5964_179
39099 5964_18
39100 5964_184
39101 5964_185
39102 5964_186
39103 5964_187
39104 5964_188
39105 5964_189
39106 5964_19
39107 5964_196
39108 5964_197
39109 5964_198
39110 5964_199
39111 5964_20
39112 5964_200
39113 5964_201
39114 5964_202
39115 5964_203
39116 5964_213
39117 5964_215
39118 5964_216
39119 5964_217
39120 5964_219
39121 5964_22
39122 5964_223
39123 5964_224
39124 5964_225
39125 5964_226
39126 5964_227
39127 5964_228
39128 5964_230
39129 5964_231
39130 5964_232
39131 5964_233
39132 5964_238
39133 5964_239
39134 5964_240
39135 5964_241
39136 5964_243
39137 5964_244
39138 5964_246
39139 5964_253
39140 5964_254
39141 5964_256
39142 5964_265
39143 5964_266
39144 5964_268
39145 5964_269
39146 5964_27
39147 5964_270
39148 5964_271
39149 5964_272
39150 5964_275
39151 5964_284
39152 5964_285
39153 5964_286
39154 5964_287
39155 5964_288
3

39895 6170_564
39896 6170_565
39897 6170_566
39898 6170_57
39899 6170_58
39900 6170_587
39901 6170_59
39902 6170_592
39903 6170_593
39904 6170_597
39905 6170_6
39906 6170_607
39907 6170_608
39908 6170_609
39909 6170_61
39910 6170_613
39911 6170_614
39912 6170_616
39913 6170_617
39914 6170_618
39915 6170_619
39916 6170_627
39917 6170_632
39918 6170_633
39919 6170_634
39920 6170_639
39921 6170_640
39922 6170_641
39923 6170_642
39924 6170_643
39925 6170_648
39926 6170_65
39927 6170_650
39928 6170_651
39929 6170_652
39930 6170_653
39931 6170_654
39932 6170_655
39933 6170_656
39934 6170_657
39935 6170_66
39936 6170_660
39937 6170_661
39938 6170_662
39939 6170_668
39940 6170_669
39941 6170_67
39942 6170_670
39943 6170_671
39944 6170_672
39945 6170_673
39946 6170_674
39947 6170_676
39948 6170_677
39949 6170_678
39950 6170_68
39951 6170_680
39952 6170_682
39953 6170_685
39954 6170_686
39955 6170_688
39956 6170_69
39957 6170_696
39958 6170_699
39959 6170_7
39960 6170_70
39961 6170_701
39962 617

40572 5976_575
40573 5976_576
40574 5976_577
40575 5976_578
40576 5976_579
40577 5976_580
40578 5976_581
40579 5976_586
40580 5976_594
40581 5976_595
40582 5976_599
40583 5976_616
40584 5976_617
40585 5976_620
40586 5976_621
40587 5976_622
40588 5976_623
40589 5976_624
40590 5976_625
40591 5976_628
40592 5976_629
40593 5976_63
40594 5976_630
40595 5976_633
40596 5976_634
40597 5976_635
40598 5976_636
40599 5976_637
40600 5976_638
40601 5976_64
40602 5976_646
40603 5976_648
40604 5976_649
40605 5976_65
40606 5976_650
40607 5976_651
40608 5976_652
40609 5976_653
40610 5976_654
40611 5976_666
40612 5976_667
40613 5976_668
40614 5976_669
40615 5976_670
40616 5976_671
40617 5976_672
40618 5976_673
40619 5976_678
40620 5976_679
40621 5976_680
40622 5976_682
40623 5976_683
40624 5976_690
40625 5976_691
40626 5976_692
40627 5976_693
40628 5976_702
40629 5976_703
40630 5976_704
40631 5976_705
40632 5976_706
40633 5976_707
40634 5976_708
40635 5976_714
40636 5976_719
40637 5976_720
40638 5976_72

In [19]:
search_tolerance = 0.0075
print("d:", geo.distance_epsg_4326(46.287235, 7.884615, 46.287235 + search_tolerance, 7.884615 + search_tolerance))
request_circles_1k = group_geo_circles(stop_regions, request_radius=1000, search_tolerance=search_tolerance)# 
print("{} request circles".format(len(request_circles_1k)))

d: 1014.402143720624
1 6015_10
2 6015_100
3 6015_101
4 6015_103
5 6015_104
6 6015_105
7 6015_106
8 6015_107
9 6015_111
10 6015_112
11 6015_113
12 6015_115
13 6015_116
14 6015_117
15 6015_118
16 6015_119
17 6015_12
18 6015_120
19 6015_121
20 6015_122
21 6015_123
22 6015_124
23 6015_125
24 6015_127
25 6015_128
26 6015_129
27 6015_130
28 6015_131
29 6015_132
30 6015_133
31 6015_134
32 6015_135
33 6015_136
34 6015_137
35 6015_138
36 6015_139
37 6015_140
38 6015_142
39 6015_143
40 6015_144
41 6015_145
42 6015_146
43 6015_147
44 6015_148
45 6015_149
46 6015_15
47 6015_150
48 6015_151
49 6015_152
50 6015_153
51 6015_154
52 6015_156
53 6015_157
54 6015_158
55 6015_159
56 6015_16
57 6015_160
58 6015_161
59 6015_162
60 6015_163
61 6015_164
62 6015_165
63 6015_166
64 6015_168
65 6015_169
66 6015_17
67 6015_170
68 6015_171
69 6015_172
70 6015_173
71 6015_174
72 6015_175
73 6015_176
74 6015_177
75 6015_179
76 6015_18
77 6015_180
78 6015_181
79 6015_183
80 6015_184
81 6015_185
82 6015_186
83 6015_18

663 6014_46
664 6014_460
665 6014_461
666 6014_462
667 6014_463
668 6014_464
669 6014_465
670 6014_466
671 6014_467
672 6014_468
673 6014_469
674 6014_47
675 6014_470
676 6014_471
677 6014_472
678 6014_473
679 6014_474
680 6014_475
681 6014_476
682 6014_477
683 6014_478
684 6014_479
685 6014_48
686 6014_480
687 6014_481
688 6014_482
689 6014_483
690 6014_486
691 6014_487
692 6014_489
693 6014_49
694 6014_490
695 6014_491
696 6014_492
697 6014_493
698 6014_494
699 6014_495
700 6014_496
701 6014_50
702 6014_503
703 6014_504
704 6014_505
705 6014_506
706 6014_507
707 6014_508
708 6014_509
709 6014_51
710 6014_510
711 6014_511
712 6014_512
713 6014_513
714 6014_515
715 6014_516
716 6014_517
717 6014_518
718 6014_519
719 6014_52
720 6014_521
721 6014_522
722 6014_524
723 6014_525
724 6014_526
725 6014_528
726 6014_53
727 6014_530
728 6014_532
729 6014_533
730 6014_534
731 6014_535
732 6014_536
733 6014_537
734 6014_538
735 6014_539
736 6014_540
737 6014_541
738 6014_542
739 6014_543
740 601

1297 6042_1390
1298 6042_1395
1299 6042_14
1300 6042_140
1301 6042_141
1302 6042_142
1303 6042_145
1304 6042_152
1305 6042_155
1306 6042_156
1307 6042_157
1308 6042_158
1309 6042_16
1310 6042_161
1311 6042_163
1312 6042_17
1313 6042_171
1314 6042_172
1315 6042_173
1316 6042_174
1317 6042_175
1318 6042_176
1319 6042_178
1320 6042_18
1321 6042_180
1322 6042_189
1323 6042_228
1324 6042_23
1325 6042_24
1326 6042_245
1327 6042_257
1328 6042_264
1329 6042_265
1330 6042_27
1331 6042_28
1332 6042_284
1333 6042_29
1334 6042_30
1335 6042_309
1336 6042_31
1337 6042_310
1338 6042_311
1339 6042_32
1340 6042_323
1341 6042_325
1342 6042_33
1343 6042_336
1344 6042_34
1345 6042_340
1346 6042_343
1347 6042_344
1348 6042_346
1349 6042_351
1350 6042_36
1351 6042_365
1352 6042_366
1353 6042_367
1354 6042_37
1355 6042_39
1356 6042_40
1357 6042_41
1358 6042_415
1359 6042_416
1360 6042_417
1361 6042_418
1362 6042_419
1363 6042_42
1364 6042_420
1365 6042_421
1366 6042_422
1367 6042_426
1368 6042_427
1369 6042_

1946 5966_802
1947 5966_803
1948 5966_806
1949 5966_809
1950 5966_81
1951 5966_810
1952 5966_811
1953 5966_812
1954 5966_813
1955 5966_814
1956 5966_815
1957 5966_816
1958 5966_817
1959 5966_818
1960 5966_822
1961 5966_823
1962 5966_824
1963 5966_825
1964 5966_826
1965 5966_827
1966 5966_830
1967 5966_831
1968 5966_834
1969 5966_835
1970 5966_836
1971 5966_838
1972 5966_839
1973 5966_840
1974 5966_841
1975 5966_846
1976 5966_849
1977 5966_850
1978 5966_855
1979 5966_857
1980 5966_858
1981 5966_859
1982 5966_862
1983 5966_863
1984 5966_867
1985 5966_868
1986 5966_87
1987 5966_870
1988 5966_871
1989 5966_872
1990 5966_873
1991 5966_874
1992 5966_877
1993 5966_879
1994 5966_88
1995 5966_880
1996 5966_881
1997 5966_882
1998 5966_885
1999 5966_886
2000 5966_887
2001 5966_889
2002 5966_890
2003 5966_891
2004 5966_892
2005 5966_896
2006 5966_897
2007 5966_899
2008 5966_90
2009 5966_901
2010 5966_906
2011 5966_907
2012 5966_909
2013 5966_91
2014 5966_910
2015 5966_913
2016 5966_914
2017 5966_9

2541 5949_215
2542 5949_216
2543 5949_217
2544 5949_218
2545 5949_220
2546 5949_225
2547 5949_226
2548 5949_227
2549 5949_228
2550 5949_229
2551 5949_230
2552 5949_231
2553 5949_232
2554 5949_233
2555 5949_234
2556 5949_235
2557 5949_236
2558 5949_237
2559 5949_239
2560 5949_241
2561 5949_242
2562 5949_243
2563 5949_244
2564 5949_245
2565 5949_246
2566 5949_247
2567 5949_249
2568 5949_25
2569 5949_255
2570 5949_256
2571 5949_257
2572 5949_259
2573 5949_26
2574 5949_260
2575 5949_261
2576 5949_262
2577 5949_263
2578 5949_264
2579 5949_265
2580 5949_266
2581 5949_267
2582 5949_27
2583 5949_271
2584 5949_272
2585 5949_275
2586 5949_276
2587 5949_278
2588 5949_28
2589 5949_281
2590 5949_282
2591 5949_283
2592 5949_284
2593 5949_285
2594 5949_286
2595 5949_287
2596 5949_288
2597 5949_289
2598 5949_296
2599 5949_297
2600 5949_298
2601 5949_299
2602 5949_30
2603 5949_300
2604 5949_301
2605 5949_303
2606 5949_31
2607 5949_32
2608 5949_320
2609 5949_321
2610 5949_322
2611 5949_323
2612 5949_324

...

37902 5940_499
37903 5940_500
37904 5940_503
37905 5940_504
37906 5940_505
37907 5940_506
37908 5940_507
37909 5940_508
37910 5940_509
37911 5940_510
37912 5940_511
37913 5940_512
37914 5940_52
37915 5940_521
37916 5940_524
37917 5940_526
37918 5940_53
37919 5940_532
37920 5940_533
37921 5940_54
37922 5940_543
37923 5940_548
37924 5940_55
37925 5940_550
37926 5940_551
37927 5940_553
37928 5940_554
37929 5940_555
37930 5940_556
37931 5940_557
37932 5940_558
37933 5940_559
37934 5940_56
37935 5940_560
37936 5940_561
37937 5940_562
37938 5940_563
37939 5940_564
37940 5940_565
37941 5940_566
37942 5940_567
37943 5940_568
37944 5940_57
37945 5940_570
37946 5940_571
37947 5940_574
37948 5940_575
37949 5940_576
37950 5940_577
37951 5940_578
37952 5940_579
37953 5940_58
37954 5940_582
37955 5940_584
37956 5940_588
37957 5940_589
37958 5940_590
37959 5940_591
37960 5940_592
37961 5940_593
37962 5940_599
37963 5940_60
37964 5940_601
37965 5940_602
37966 5940_603
37967 5940_604
37968 5940_605
379

38525 6106_711
38526 6106_712
38527 6106_713
38528 6106_714
38529 6106_715
38530 6106_716
38531 6106_718
38532 6106_719
38533 6106_72
38534 6106_720
38535 6106_73
38536 6106_74
38537 6106_741
38538 6106_742
38539 6106_746
38540 6106_747
38541 6106_749
38542 6106_75
38543 6106_750
38544 6106_751
38545 6106_752
38546 6106_753
38547 6106_754
38548 6106_755
38549 6106_756
38550 6106_757
38551 6106_758
38552 6106_759
38553 6106_76
38554 6106_760
38555 6106_761
38556 6106_762
38557 6106_763
38558 6106_766
38559 6106_769
38560 6106_77
38561 6106_774
38562 6106_775
38563 6106_776
38564 6106_777
38565 6106_778
38566 6106_779
38567 6106_78
38568 6106_780
38569 6106_781
38570 6106_782
38571 6106_783
38572 6106_784
38573 6106_789
38574 6106_79
38575 6106_790
38576 6106_791
38577 6106_792
38578 6106_797
38579 6106_798
38580 6106_799
38581 6106_80
38582 6106_800
38583 6106_801
38584 6106_802
38585 6106_809
38586 6106_81
38587 6106_819
38588 6106_82
38589 6106_820
38590 6106_826
38591 6106_827
38592 

39094 5964_171
39095 5964_172
39096 5964_173
39097 5964_176
39098 5964_179
39099 5964_18
39100 5964_184
39101 5964_185
39102 5964_186
39103 5964_187
39104 5964_188
39105 5964_189
39106 5964_19
39107 5964_196
39108 5964_197
39109 5964_198
39110 5964_199
39111 5964_20
39112 5964_200
39113 5964_201
39114 5964_202
39115 5964_203
39116 5964_213
39117 5964_215
39118 5964_216
39119 5964_217
39120 5964_219
39121 5964_22
39122 5964_223
39123 5964_224
39124 5964_225
39125 5964_226
39126 5964_227
39127 5964_228
39128 5964_230
39129 5964_231
39130 5964_232
39131 5964_233
39132 5964_238
39133 5964_239
39134 5964_240
39135 5964_241
39136 5964_243
39137 5964_244
39138 5964_246
39139 5964_253
39140 5964_254
39141 5964_256
39142 5964_265
39143 5964_266
39144 5964_268
39145 5964_269
39146 5964_27
39147 5964_270
39148 5964_271
39149 5964_272
39150 5964_275
39151 5964_284
39152 5964_285
39153 5964_286
39154 5964_287
39155 5964_288
39156 5964_289
39157 5964_291
39158 5964_292
39159 5964_293
39160 5964_299


39651 6170_182
39652 6170_183
39653 6170_184
39654 6170_185
39655 6170_186
39656 6170_188
39657 6170_192
39658 6170_193
39659 6170_194
39660 6170_196
39661 6170_2
39662 6170_20
39663 6170_200
39664 6170_201
39665 6170_202
39666 6170_208
39667 6170_209
39668 6170_21
39669 6170_210
39670 6170_211
39671 6170_212
39672 6170_213
39673 6170_214
39674 6170_217
39675 6170_218
39676 6170_219
39677 6170_22
39678 6170_221
39679 6170_23
39680 6170_230
39681 6170_231
39682 6170_232
39683 6170_233
39684 6170_238
39685 6170_239
39686 6170_24
39687 6170_240
39688 6170_25
39689 6170_253
39690 6170_254
39691 6170_257
39692 6170_258
39693 6170_26
39694 6170_263
39695 6170_266
39696 6170_267
39697 6170_268
39698 6170_27
39699 6170_270
39700 6170_272
39701 6170_273
39702 6170_274
39703 6170_277
39704 6170_278
39705 6170_28
39706 6170_280
39707 6170_281
39708 6170_282
39709 6170_287
39710 6170_289
39711 6170_29
39712 6170_290
39713 6170_291
39714 6170_292
39715 6170_293
39716 6170_294
39717 6170_295
39718 6

40245 5976_1183
40246 5976_1184
40247 5976_1185
40248 5976_1186
40249 5976_1187
40250 5976_1188
40251 5976_1190
40252 5976_120
40253 5976_1202
40254 5976_1204
40255 5976_1205
40256 5976_1206
40257 5976_1208
40258 5976_121
40259 5976_1214
40260 5976_1215
40261 5976_1216
40262 5976_1217
40263 5976_1218
40264 5976_1219
40265 5976_122
40266 5976_1220
40267 5976_1221
40268 5976_1227
40269 5976_1228
40270 5976_1229
40271 5976_1232
40272 5976_1241
40273 5976_1242
40274 5976_1243
40275 5976_1247
40276 5976_1248
40277 5976_1249
40278 5976_1250
40279 5976_1263
40280 5976_1264
40281 5976_1266
40282 5976_1271
40283 5976_1273
40284 5976_1274
40285 5976_1275
40286 5976_1276
40287 5976_1277
40288 5976_1292
40289 5976_1293
40290 5976_1295
40291 5976_1296
40292 5976_1298
40293 5976_1299
40294 5976_1300
40295 5976_1301
40296 5976_1309
40297 5976_1310
40298 5976_1314
40299 5976_1333
40300 5976_1334
40301 5976_1335
40302 5976_1336
40303 5976_1337
40304 5976_1347
40305 5976_1348
40306 5976_1349
40307 5976_

In [ ]:
# def plot_radius_n_request(radius_range=None):
#     rad_reqs = [{"radius_m": 50, "n_requests": 44690},
#     {"radius_m": 75, "n_requests": 12318},
#     {"radius_m": 100, "n_requests": 8564},
#     {"radius_m": 200, "n_requests": 5134},
#     {"radius_m": 300, "n_requests": 3868},
#     {"radius_m": 400, "n_requests": 3178},
#     {"radius_m": 500, "n_requests": 2831},
#     {"radius_m": 800, "n_requests": 2060},
#     {"radius_m": 1000, "n_requests": 1884}]
    
#     rad_reqs = pd.DataFrame(rad_reqs)
#     if not radius_range is None:
#         rad_reqs = rad_reqs[(rad_reqs['radius_m'] >= radius_range[0]) & (rad_reqs['radius_m'] <= radius_range[1])]
        
#     print(rad_reqs)
    
#     p = figure(plot_width=400, plot_height=300)
#     p.line(rad_reqs["radius_m"], rad_reqs["n_requests"], color="blue", alpha=0.8, line_width=2)
#     p.circle(rad_reqs["radius_m"], rad_reqs["n_requests"], color="navy", fill_alpha=1, size=4)
    
#     return p    

In [ ]:
# p = plot_radius_n_request()
# show(p)
# p = plot_radius_n_request(radius_range=(200, 1000))
# show(p)

In [ ]:
def summary_request_circles(request_circle_list, range_hist=(0,100)):
    sr_inside_request_circle = []
    for rc in request_circle_list:
        sr_inside_request_circle.append(len(rc.sr))

    print(pd.Series(sr_inside_request_circle).describe())
    pd.Series(sr_inside_request_circle).plot.hist(range=range_hist, bins=100)
    
def greatest_request_circle(request_circle_list):
    request_circle = request_circle_list[0]
    
    for rc in request_circle_list:
        if len(rc.sr) > len(request_circle.sr):
            request_circle = rc
    return 

In [ ]:
print("Request radius: 200\n")
summary_request_circles(request_circles_200)

In [ ]:
print("Request radius: 400\n")
summary_request_circles(request_circles_400)

In [ ]:
print("Request radius: 800\n")
summary_request_circles(request_circles_800)

In [ ]:
print("Request radius: 1000\n")
summary_request_circles(request_circles_1k)

In [ ]:
total = 0
for rc in request_circles_200:
    total = total + len(rc.sr)
total

In [ ]:
srs = pd.Series()
for rc in request_circles_200:
    srs = srs.append(rc.sr['sr_id'])

len(srs.drop_duplicates())

In [ ]:
len(request_circles_50)